### Запуск QtLab

In [1]:
%matplotlib qt5
from qsweepy import *
from qsweepy.instruments import *
from qsweepy.save_pkl import save_pkl
import matplotlib.pyplot as plt
import numpy as np
from matplotlib import interactive
interactive(True)

Failed loading module Keysight_M3102A:  No module named 'keysightSD1'
Failed loading module Keysight_M3202A:  No module named 'keysightSD1'


In [2]:
from resonator_tools import circuit

In [3]:
from qsweepy.paramp import paramp

In [4]:
import imp
import qsweepy.paramp
imp.reload(qsweepy.paramp)
imp.reload(sweep)

<module 'qsweepy.sweep' from 'D:\\qtlab_replacement\\qsweepy\\sweep.py'>

In [5]:
sample_name = 'Parametric-Takmakov-Aluminum-1909.072.1-2'

In [6]:
from qsweepy.ponyfiles import *
db = database.MyDatabase()
sweeper = sweep_extras.Sweeper(db, sample_name=sample_name)
exdir_db_inst = exdir_db.Exdir_db(db=db, sample_name=sample_name)

## Device initialization

In [7]:
#dac = nndac('TCPIP0::10.20.61.12::1000::SOCKET')

In [8]:
bias = Yokogawa_GS210(address = 'GPIB1::1::INSTR')

#rf_switch = nn_rf_switch(name='rf_switch', address='10.20.61.224')
pna = Agilent_N5242A('pna', address = 'TCPIP0::10.20.61.48::inst0::INSTR')
lo1 = Agilent_E8257D('lo1', address = 'TCPIP0::10.20.61.59::inst0::INSTR')
#sa = Agilent_N9030A('pxa', address = 'TCPIP0::10.20.61.56::inst0::INSTR')

In [9]:
pna.set_status(1)

True

# Спектроскопия

In [9]:
pna.set_xlim(4e9, 10e9)
diap = np.linspace(-4,4, 401)
#dac.set_status(1)
#current_src.set_range(0.1)
pna.set_power(-45)
pna.set_nop(601)
pna.set_bandwidth(1000)
lo1.set_status(0)
sweep.sweep(pna,(diap,lambda x: dac.set_voltage(x,channel=2),"Voltage", "V"), filename=sample_name+" spectrum")

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


HTML(value='')

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


Started at:  Oct 18 2018 07:34:08
Exiting sweep main thread #{} via return 9020

Elapsed time: 0 h 4 m 52.56 s


{'S-parameter': (('Voltage', 'Frequency'),
  (array([-4.  , -3.98, -3.96, -3.94, -3.92, -3.9 , -3.88, -3.86, -3.84,
          -3.82, -3.8 , -3.78, -3.76, -3.74, -3.72, -3.7 , -3.68, -3.66,
          -3.64, -3.62, -3.6 , -3.58, -3.56, -3.54, -3.52, -3.5 , -3.48,
          -3.46, -3.44, -3.42, -3.4 , -3.38, -3.36, -3.34, -3.32, -3.3 ,
          -3.28, -3.26, -3.24, -3.22, -3.2 , -3.18, -3.16, -3.14, -3.12,
          -3.1 , -3.08, -3.06, -3.04, -3.02, -3.  , -2.98, -2.96, -2.94,
          -2.92, -2.9 , -2.88, -2.86, -2.84, -2.82, -2.8 , -2.78, -2.76,
          -2.74, -2.72, -2.7 , -2.68, -2.66, -2.64, -2.62, -2.6 , -2.58,
          -2.56, -2.54, -2.52, -2.5 , -2.48, -2.46, -2.44, -2.42, -2.4 ,
          -2.38, -2.36, -2.34, -2.32, -2.3 , -2.28, -2.26, -2.24, -2.22,
          -2.2 , -2.18, -2.16, -2.14, -2.12, -2.1 , -2.08, -2.06, -2.04,
          -2.02, -2.  , -1.98, -1.96, -1.94, -1.92, -1.9 , -1.88, -1.86,
          -1.84, -1.82, -1.8 , -1.78, -1.76, -1.74, -1.72, -1.7 , -1.68,
        

#### Autocalibrate

In [10]:
p = paramp(bias_src=bias, vna=pna, pump_src=lo1)
#p.voltage_setter = lambda x: bias.set_current(x)
p.voltage_getter = lambda: bias.get_current()
def current_setter(x):
    bias.set_current(x)
    time.sleep(0.2)
def power_setter(x):
    lo1.set_status(0)
    lo1.set_power(x)
    time.sleep(0.2)
    lo1.set_status(1)
p.power_setter = power_setter
p.voltage_setter = current_setter

In [20]:
p.set_target_f(9.25e9)
p.set_target_bw(5e6)
p.set_target_power(-20)
p.hint_nop = 4000
p.hint_maxfun = 20
p.hint_rel_errors = (1e-2, 2e-1, 2e-1)
p.hint_abs_errors = (0.5, 5e-4)
p.bounds = ((-10,5),(-7.5e-3,7.5e-3))
p.num_restarts = 6
p.optimize_pump_frequency = False

In [21]:
p.measure()

root: WARNING  Setting a boolean, but that is not the expected type


Gain, dB: -18.682395766768188 SNR, dB: 1.7977344062245142
[-1.58, -0.0008]


C:\ProgramData\Anaconda3\lib\site-packages\scipy\optimize\_minimize.py:516: RuntimeWarning:

Method Nelder-Mead cannot handle constraints nor bounds.



Gain, dB: -13.894398468987852 SNR, dB: 3.8975663266155665
[-1.08e+00 -8.00e-04] 0.4076086270967253
Gain, dB: -17.680411075132554 SNR, dB: 2.276194426305835
[-1.58e+00 -3.00e-04] 0.5920802265394022
Gain, dB: -18.576201335476973 SNR, dB: 1.8872823793605926
[-1.58e+00 -8.00e-04] 0.6475476953826763
Gain, dB: -12.37889246729486 SNR, dB: 4.440157600836142
[-1.08e+00 -3.00e-04] 0.3597362804728799
Gain, dB: -10.411949329064944 SNR, dB: 5.108070239272316
[-8.3e-01 -5.0e-05] 0.3084558250206651
Gain, dB: -11.299075839317098 SNR, dB: 4.74478242401903
[-0.33    -0.00055] 0.33536810554286506
Gain, dB: -13.98748877069024 SNR, dB: 3.7918189109955454
[-0.08    0.0002] 0.41765540768413645
Gain, dB: -10.028936540666075 SNR, dB: 5.313585279304997
[-8.3e-01 -5.5e-04] 0.2941991895880202
Gain, dB: -13.783182024696007 SNR, dB: 3.9236159576975975
[-1.33e+00 -5.00e-05] 0.405171047518981
Gain, dB: -10.373790195354122 SNR, dB: 5.067765309785419
[-5.80e-01 -4.25e-04] 0.3113317902791752
Gain, dB: -11.33862344732431

Gain, dB: -9.696960562253594 SNR, dB: 5.3084781737107765
[-7.831250e-01 -5.109375e-04] 0.2945453579543145
Gain, dB: -9.687876980841793 SNR, dB: 5.409986208128801
[-7.5968750e-01 -5.2265625e-04] 0.2877407552491959
Gain, dB: -10.016540950372208 SNR, dB: 5.216286998917024
[-7.5968750e-01 -2.7265625e-04] 0.3008647446790275
Gain, dB: -9.728743982771862 SNR, dB: 5.324701594897916
[-7.65546875e-01 -5.50976562e-04] 0.29344711254615263
Gain, dB: -9.809255387158034 SNR, dB: 5.334063935969331
[-7.63593750e-01 -4.58203125e-04] 0.29281519275870144
Gain, dB: -9.731341516632694 SNR, dB: 5.332702584184954
[-7.63593750e-01 -5.83203125e-04] 0.29290699382578295
Gain, dB: -9.650204735402959 SNR, dB: 5.397096051115433
[-7.5968750e-01 -5.2265625e-04] 0.2885960581453856
Gain, dB: -9.718074761249206 SNR, dB: 5.345710568156527
[-0.7596875000000004, -0.0005226562499999999]
Gain, dB: -11.79478216338607 SNR, dB: 4.585309307847889
[-0.2596875  -0.00052266] 0.34791172822762173
Gain, dB: -10.718719867740544 SNR, dB:

{'S-parameter': array(-0.325073-0.01016503j),
 'SNR': array(3.48183086),
 'Pump_power': array(-0.7596875),
 'Bias': array(-0.00052266)}

In [33]:
pna.set_bandwidth(5e6)
pna.get_bandwidth()

5000000.0

In [12]:
lo1.set_power(-5)
bias.set_current(-3.5e-3)

True

In [22]:
#lo1.set_frequency(9.2e9)
#lo1.set_power(3.5)
#dac.set_voltage(1.0, channel=2)
target_f = np.linspace(9.25e9, 8.75e9, 51)
def target_setter(f):
    p.set_target_f(f)
    lo1.set_power(lo1.get_power()-1.0) # go by 1dB down so we don't inflate pump powers to infinity
    bias.set_current(bias.get_current())
    # this is kostyl
calibration = sweeper.sweep(p, 
                          (target_f, target_setter, 'Target frequency', 'Hz'), 
                          measurement_type='paramp_fixed_frequency_calibration',
                          metadata = {'target_bw':p.target_bw,
                                      'target_power':p.target_power})

root: WARNING  Setting a boolean, but that is not the expected type


Gain, dB: -19.29758387938928 SNR, dB: 1.584889471518456
[-1.76, -0.0005226]
Gain, dB: -15.630950404330221 SNR, dB: 3.151288746297061
[-1.260e+00 -5.226e-04] 0.48402871326651137
Gain, dB: -17.422044758559036 SNR, dB: 2.3815642209636447
[-1.76e+00 -2.26e-05] 0.5778878690461545
Gain, dB: -19.279469527604345 SNR, dB: 1.5918424642850717
[-1.760e+00 -5.226e-04] 0.6931316873103929
Gain, dB: -12.414867411391208 SNR, dB: 4.496688677218456
[-1.26e+00 -2.26e-05] 0.3550840234989658
Gain, dB: -10.948035030758302 SNR, dB: 4.922411820668912
[-1.010e+00  2.274e-04] 0.32192804923566304
Gain, dB: -11.051780560688398 SNR, dB: 4.873061532640776
[-5.100e-01 -2.726e-04] 0.3256070853361394
Gain, dB: -14.267792922958973 SNR, dB: 3.6939102281724256
[-0.26       0.0004774] 0.4271780974669773
Gain, dB: -12.692552238450256 SNR, dB: 4.305706753684641
[-5.100e-01  2.274e-04] 0.3710473418007135
Gain, dB: -10.849224836821898 SNR, dB: 4.984199347170075
[-1.010e+00 -2.726e-04] 0.31738037232408994
Gain, dB: -15.41912750

Gain, dB: -10.20647540114863 SNR, dB: 5.20292404169324
[-0.83714844 -0.00147817] 0.3017919115092702
Gain, dB: -10.711271972784207 SNR, dB: 5.05485472627806
[-0.64964844 -0.00144692] 0.3122586856601218
Gain, dB: -9.631048665648935 SNR, dB: 5.42649596914237
[-0.74339844 -0.00083754] 0.2866489815497797
Gain, dB: -10.264641347410677 SNR, dB: 5.237736623456829
[-0.86839844 -0.00102504] 0.29938244967938205
Gain, dB: -9.697909764344638 SNR, dB: 5.363260541272286
[-0.70433594 -0.00096645] 0.290853266673272
Gain, dB: -9.80012301018576 SNR, dB: 5.369530565911099
[-0.81371094 -0.00100551] 0.290433657070468
Gain, dB: -9.80638139078205 SNR, dB: 5.393852744202718
[-0.78636719 -0.00099574] 0.28881166189363205
Gain, dB: -9.66310288601141 SNR, dB: 5.364191110686067
[-7.55117187e-01 -6.98869531e-04] 0.2907909517763673
Gain, dB: -9.737588151581178 SNR, dB: 5.355291967773626
[-0.76976562 -0.00102553] 0.29138742340614426
Gain, dB: -9.67378415010687 SNR, dB: 5.365646067669736
[-0.76488281 -0.00091664] 0.290

root: WARNING  Setting a boolean, but that is not the expected type


Gain, dB: -21.153404876450878 SNR, dB: 0.6018090934830235
[-1.76, -0.0007047]
Gain, dB: -20.86478593682344 SNR, dB: 0.7682768794357977
[-1.260e+00 -7.047e-04] 0.8378616488329585
Gain, dB: -21.2559973004808 SNR, dB: 0.6237920620416944
[-1.760e+00 -2.047e-04] 0.8662052144384264
Gain, dB: -21.3820530040744 SNR, dB: 0.5509878514768395
[-1.760e+00 -7.047e-04] 0.880848491357032
Gain, dB: -20.32009366049362 SNR, dB: 1.073928696824614
[-1.260e+00 -2.047e-04] 0.7809210513867644
Gain, dB: -18.486701884834435 SNR, dB: 1.7926300217499371
[-1.01e+00  4.53e-05] 0.6618155967986568
Gain, dB: -16.964286743682443 SNR, dB: 2.49100031634154
[-5.100e-01 -4.547e-04] 0.5635078473540394
Gain, dB: -10.128193591671387 SNR, dB: 5.150043270780937
[ 0.115     -0.0005797] 0.3054890675765982
Gain, dB: -13.206867732908156 SNR, dB: 4.0207846192003664
[3.650e-01 1.703e-04] 0.3962064470531786
Gain, dB: -15.567205768795242 SNR, dB: 3.065400795911244
[ 1.490e+00 -4.547e-04] 0.49369635455516603
Gain, dB: -14.17311060879648

...

Gain, dB: -19.442365061505026 SNR, dB: 0.52530049263357
[-3.33, 0.0055757]
Gain, dB: -19.186955851674703 SNR, dB: 0.5838500230235666
[-2.83       0.0055757] 0.8742084453347725
Gain, dB: -13.729661487610274 SNR, dB: 3.0684145966422616
[-3.33       0.0060757] 0.4933538712061336
Gain, dB: -19.38790890604045 SNR, dB: 0.509155632833475
[-3.33       0.0055757] 0.8893740155694911
Gain, dB: -14.455486090595716 SNR, dB: 2.772617444634223
[-2.83       0.0060757] 0.5281268596432022
Gain, dB: -18.005779956200158 SNR, dB: 1.1402016611600205
[-3.33       0.0065757] 0.7690947271605499
Gain, dB: -16.685249034647953 SNR, dB: 1.815903016116609
[-3.205      0.0063257] 0.6582785417347671
Gain, dB: -8.478013069135617 SNR, dB: 5.158704209984286
[-2.955      0.0058257] 0.30488045156084265
Gain, dB: -19.031713655736247 SNR, dB: 0.7199935817802251
[-2.83       0.0055757] 0.8472286662163164
Gain, dB: -9.07395422275562 SNR, dB: 5.00191821947764
[-3.455      0.0058257] 0.3160881233681442
Gain, dB: -19.31171788900

Gain, dB: -12.177986244802703 SNR, dB: 3.6791834660589844
[-2.82023437  0.00571242] 0.42862910104588087
Gain, dB: -6.17639776343465 SNR, dB: 5.856331146439083
[-2.54484375  0.00572414] 0.2596371811230701
Gain, dB: -9.479023723293782 SNR, dB: 4.534083991552237
[-2.7284375   0.00571632] 0.35203966645754153
Gain, dB: -5.810233219656153 SNR, dB: 5.994422725493299
[-2.59074219  0.00572218] 0.25151143057253483
Gain, dB: -6.012359391717268 SNR, dB: 5.81421648921399
[-2.32511719  0.00569093] 0.262167197188059
Gain, dB: -5.771552587394014 SNR, dB: 6.065026764485325
[-2.65836914  0.00572463] 0.2474556211214305
Gain, dB: -5.489314342637455 SNR, dB: 6.070032558523294
[-2.50382812  0.00570461] 0.24717056148736008
Gain, dB: -5.515424485096454 SNR, dB: 6.076643745069756
[-2.503828124999999, 0.005704606249999998]
Gain, dB: -9.397570798694279 SNR, dB: 4.683426928529478
[-2.00382812  0.00570461] 0.34013968654140064
Gain, dB: -16.07747213574303 SNR, dB: 2.0981703064268133
[-2.50382812  0.00620461] 0.6168

root: WARNING  Setting a boolean, but that is not the expected type


Gain, dB: -19.2140443384113 SNR, dB: 0.5785157808305625
[-3.66, 0.0057246]
Gain, dB: -18.989060942405484 SNR, dB: 0.8001026736797068
[-3.16       0.0057246] 0.8317441072015398
Gain, dB: -13.967087882207188 SNR, dB: 3.0418033032902203
[-3.66       0.0062246] 0.4963861662465666
Gain, dB: -19.21532672044371 SNR, dB: 0.6075978862175211
[-3.66       0.0057246] 0.8694411904469648
Gain, dB: -14.652630404212516 SNR, dB: 2.656081134161648
[-3.16       0.0062246] 0.5424901868264307


KeyboardInterrupt: 

In [11]:
calibration = exdir_db_inst.select_measurement_by_id(4140)
p.load_calibration(calibration)

Exdir_db.select_measurement_by_id: trying to load measurement state by id:  d:\data\2019-10-25\004140-paramp_fixed_frequency_calibration-Parametric-Takmakov-Aluminum-1909.072.2-7


In [12]:
p.set_target_freq_calib(8e9)

In [12]:
lo1.set_frequency(5.001e9)
lo1.set_power(-8.5)
dac.set_voltage(1.25, channel=2)
target_f = np.linspace(5e9, 8e9, 301)
four_wave_calibration = sweep.sweep(p, (target_f, lambda x: (p.set_target_f(x), lo1.set_frequency(x+0.001e9)), 'Target frequency', 'Hz'), filename='Four-wave calibration', output=False)

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


HTML(value='')

C:\ProgramData\Anaconda3\lib\site-packages\numpy\lib\function_base.py:2185: RuntimeWarning: invalid value encountered in remainder
  ddmod = mod(dd + pi, 2*pi) - pi
C:\ProgramData\Anaconda3\lib\site-packages\numpy\lib\function_base.py:2186: RuntimeWarning: invalid value encountered in greater
  _nx.copyto(ddmod, pi, where=(ddmod == -pi) & (dd > 0))
C:\ProgramData\Anaconda3\lib\site-packages\numpy\lib\function_base.py:2188: RuntimeWarning: invalid value encountered in less
  _nx.copyto(ph_correct, 0, where=abs(dd) < discont)


Started at:  Oct 19 2018 14:42:43


C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


...

-1.3839329249824304 -8.954803764937939
[ 7.25335556e+09 -7.59111111e+00 -6.19111111e-01] 0.1272095228146499
-0.1288640001540444 -9.534304492844793
[ 7.78408889e+09 -6.09777778e+00 -5.12977778e-01] 0.11131906520484366
3.299716960693111 -11.189028224766231
[ 7.43026667e+09 -7.09333333e+00 -5.83733333e-01] 0.07604964262159955
4.043229227851786 -11.489388125453848
[ 7.25335556e+09 -6.09777778e+00 -6.45644444e-01] 0.07096777469360449
-1.2019675609781997 -8.973106077790368
[ 7.10003259e+09 -6.05629630e+00 -7.84207407e-01] 0.12667455643087502
3.4788984166556682 -11.267937204976462
[ 7.50692815e+09 -6.55407407e+00 -5.54251852e-01] 0.07468033879491053
3.630020168806169 -11.297163170351684
[ 7.36343358e+09 -5.32345679e+00 -6.58419753e-01] 0.07417946264227689
1.0518966293611247 -7.716565540029039
[ 7.19110905e+09 -5.04230453e+00 -7.57346502e-01] 0.1691778284106646
4.4128738615614855 -11.657339128325091
[ 7.42797337e+09 -6.17613169e+00 -6.05025514e-01] 0.06827568832038189
4.80437656510224 -11.8743

5.603514115837237 -11.59672622455284
[ 7.09419000e+09 -5.62133333e+00 -9.46111111e-01] 0.06923526798542907
2.821847200624294 -10.898538233320828
[ 7.51931000e+09 -6.46755556e+00 -6.66851852e-01] 0.08131041481340393
1.661676060258857 -8.727812475833874
[ 7.14068750e+09 -5.69688889e+00 -9.46712963e-01] 0.13403516472594545
4.623746724714176 -11.755732845539
[ 7.35324750e+09 -6.12000000e+00 -8.07083333e-01] 0.06674622612616181
5.18945089327482 -12.045407693913784
[ 7.22039750e+09 -5.75733333e+00 -8.79305556e-01] 0.06243947324781326
6.770070358453042 -11.84324053025149
[ 7.18054250e+09 -5.66666667e+00 -9.26250000e-01] 0.0654147893149322
-0.35616409672133204 -6.703228477421716
[ 7.14511583e+09 -5.42488889e+00 -9.38287037e-01] 0.2136373352434798
4.798992334654912 -11.868532244728309
[ 7.30121458e+09 -5.94622222e+00 -8.39884259e-01] 0.06503494473480079
2.7927109565881287 -9.998681814132874
[ 7.12149806e+09 -5.68681481e+00 -9.51126543e-01] 0.1000303569580666
4.745764446063799 -11.86714855071604

2.4412810265349356 -10.802796316381237
[ 7.36078777e+09 -6.86566644e+00 -9.78672560e-01] 0.08312283910485826
2.611318029717152 -10.73693571216644
[ 7.37807727e+09 -6.41563964e+00 -1.00086508e+00] 0.08439300064826012
2.568808776078238 -10.925157358025029
[ 7.33478458e+09 -6.52394098e+00 -1.00654254e+00] 0.0808135647383533
1.8962647543332356 -10.481436945333337
[ 7.32345851e+09 -6.91373697e+00 -9.91167860e-01] 0.08950685662073901
2.6408860611519054 -10.829999000347412
[ 7.36442258e+09 -6.54016397e+00 -9.98440775e-01] 0.08260381397133888
2.783931774713466 -10.94795419174202
[ 7.34317121e+09 -6.24670852e+00 -1.02653919e+00] 0.08039047241913841
2.7683651034585814 -10.915808183863104
[ 7.33436294e+09 -5.93722956e+00 -1.05047250e+00] 0.08098772166240265
2.538038510970819 -10.805397353624365
[ 7.32536883e+09 -6.37657402e+00 -1.02550325e+00] 0.08307307083050884
2.6338605646744853 -10.818131723748973
[ 7.35465914e+09 -6.49926648e+00 -1.00520639e+00] 0.08282984098783394
2.6835713567123047 -10.868

-0.2689831451971449 -9.391192016413136
[ 6.67037927e+09 -9.08548955e+00 -1.59063295e+00] 0.11504845698931558
-0.27860397844358276 -9.48161633653102
[ 6.67525604e+09 -9.00959660e+00 -1.59139976e+00] 0.11267780192484127
-0.26880622016318234 -9.421576181113963
[ 6.66864127e+09 -8.92257156e+00 -1.60340366e+00] 0.11424636262281321
-0.2611142258302348 -9.513022166574128
[ 6.66907577e+09 -8.96330105e+00 -1.60021098e+00] 0.11186591604940524
-0.25271919578389557 -9.39366283474123
[ 6.66983899e+09 -8.99716823e+00 -1.59128479e+00] 0.11498302143794556
-0.26771293892254683 -9.428000629730459
[ 6.66931418e+09 -8.99318417e+00 -1.59912281e+00] 0.11407748475088465
-0.28442959967743586 -9.381567924146948
[ 6.67216591e+09 -8.98644883e+00 -1.59580537e+00] 0.11530369042026205
-0.2616215302023331 -9.466438286285051
[ 6.66660566e+09 -8.98696998e+00 -1.59906532e+00] 0.11307228571734293
-0.25485683543854404 -9.507725326433397
[ 6.66910751e+09 -8.97757860e+00 -1.60097323e+00] 0.1120024357122458
-0.2277264940778

-1.1140974275662414 -9.03862007230633
[ 7.86304725e+09 -9.17520826e+00 -1.91282994e+00] 0.12477799209714405
-1.1254718256210314 -9.045093667519238
[ 7.86285451e+09 -9.17886555e+00 -1.91309206e+00] 0.1245921365268724
Exiting sweep main thread #{} via return 14044

Elapsed time: 3 h 7 m 51.56 s


In [13]:
p.load_calibration(path=r'C:\Data\2018-10-18\14-49-39-Three-wave calibration', name='Three-wave calibration')

In [13]:
p.load_calibration(path=r'C:\Data\2018-10-19\11-11-56-Four-wave calibration', name='Four-wave calibration')
p.load_calibration(path=r'C:\Data\2018-10-19\14-42-43-Four-wave calibration', name='Four-wave calibration')

In [16]:
sa.get_sweep_time()

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


301993.3774

# Noise measurements

In [15]:
noises = []
#target_f = np.linspace(4.35e9, 4.75e9, 41)

# Gain saturation
pna.set_nop(1)
pna.set_bandwidth(1e3)
probe_powers = np.linspace(-75, -40, 36)
sweep.sweep(pna, (target_f, lambda x: (p.set_target_freq_calib(x), pna.set_centerfreq(x)), 'Target frequency', 'Hz'), \
            (probe_powers, pna.set_power, 'Probe power'), \
            filename='VNA Gain Saturation')

pna.set_power(-50)
pna.set_nop(601)
pna.set_xlim(np.min(target_f), np.max(target_f))
sweep.sweep(pna, (target_f, p.set_target_freq_calib, 'Target frequency', 'Hz'), \
            filename='VNA Monochromatic Gain')



pna.set_power(-95)
noises = []
#target_f = np.linspace(4.35e9, 4.75e9, 41)
sa.set_nop(601)
sa.set_bandwidth(1e6)
sa.set_bandwidth_video(10)
sa.set_xlim(np.min(target_f), np.max(target_f))
# switch to warm load
#rf_switch.do_set_switch(4, channel=1)
#print (rf_switch.do_get_switch(channel=1))
#time.sleep(900)
noises.append(sweep.sweep(sa,  (target_f, p.set_target_freq_calib, 'Target frequency'), \
                        filename=sample_name+' switch 4 (room -60 dB)'))

# switch to warm load
rf_switch.do_set_switch(1, channel=1)
print (rf_switch.do_get_switch(channel=1))
time.sleep(900)
#noises.append(sweep.sweep(sa, (pump_powers, lo1.set_power, 'Excitation power'), \
#                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1 Still 6dB'.format(pump_freq/1e9)))
noises.append(sweep.sweep(sa,  (target_f, p.set_target_freq_calib, 'Target frequency'), \
                        filename=sample_name+' switch 1 Still 6dB'))

rf_switch.do_set_switch(2, channel=1)
print (rf_switch.do_get_switch(channel=1))
time.sleep(900)
noises.append(sweep.sweep(sa,  (target_f, p.set_target_freq_calib, 'Target frequency'), \
                        filename=sample_name+' switch 2 MC'))




C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


HTML(value='')

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


Started at:  Oct 19 2018 17:50:42
Exiting sweep main thread #{} via return 3924

Elapsed time: 0 h 8 m 11.24 s


HTML(value='')

...

Exiting sweep main thread #{} via return 4964

Elapsed time: 0 h 3 m 43.35 s


HTML(value='')

Started at:  Oct 19 2018 18:02:45


C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)
Exception in thread Thread-12:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 916, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 864, in run
    self._target(*self._args, **self._kwargs)
  File "C:\qtlab_replacement\qsweepy\sweep.py", line 279, in main_sweep_loop
    mpoint = measurer.measure()
  File "C:\qtlab_replacement\qsweepy\instrument_drivers\Agilent_N9030A.py", line 260, in measure
    return {'Power':self.get_tracedata()[1]}
  File "C:\qtlab_replacement\qsweepy\instrument_drivers\Agilent_N9030A.py", line 205, in get_tracedata
    while int(self.ask("*ESR?"))==0:
  File "C:\qtlab_replacement\qsweepy\instrument_drivers\Agilent_N9030A.py", line 700, in ask
    return self._visainstrument

KeyboardInterrupt: 

In [31]:
sa._visainstrument.write('SYST:PRES')
sa.set_nop(601)
sa.set_bandwidth(1e6)
sa.set_bandwidth_video(5e2)
sa.set_xlim(np.min(target_f), np.max(target_f))
sa.get_sweep_time(),sa._visainstrument.timeout

Exception in thread Thread-15:
Traceback (most recent call last):
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 916, in _bootstrap_inner
    self.run()
  File "C:\ProgramData\Anaconda3\lib\threading.py", line 864, in run
    self._target(*self._args, **self._kwargs)
  File "C:\qtlab_replacement\qsweepy\sweep.py", line 281, in main_sweep_loop
    set_single_measurement_result(mpoint, indeces)
  File "C:\qtlab_replacement\qsweepy\sweep.py", line 225, in set_single_measurement_result
    ascii_file.write(data_to_str(fmt(mpoint_m_flat))+'\n')
ValueError: I/O operation on closed file.

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


(4586.76, 240000)

In [32]:
noises = []
#target_f = np.linspace(4.35e9, 4.75e9, 41)

# switch to warm load
#rf_switch.do_set_switch(4, channel=1)
#print (rf_switch.do_get_switch(channel=1))
#time.sleep(900)
noises.append(sweep.sweep(sa,  (target_f, p.set_target_freq_calib, 'Target frequency'), \
                        filename=sample_name+' switch 4 (room -60 dB)'))

# switch to warm load
rf_switch.do_set_switch(1, channel=1)
print (rf_switch.do_get_switch(channel=1))
time.sleep(900)
#noises.append(sweep.sweep(sa, (pump_powers, lo1.set_power, 'Excitation power'), \
#                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1 Still 6dB'.format(pump_freq/1e9)))
noises.append(sweep.sweep(sa,  (target_f, p.set_target_freq_calib, 'Target frequency'), \
                        filename=sample_name+' switch 1 Still 6dB'))

rf_switch.do_set_switch(2, channel=1)
print (rf_switch.do_get_switch(channel=1))
time.sleep(900)
noises.append(sweep.sweep(sa,  (target_f, p.set_target_freq_calib, 'Target frequency'), \
                        filename=sample_name+' switch 2 MC'))




HTML(value='')

Started at:  Oct 20 2018 03:10:21


C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


Exiting sweep main thread #{} via return 3340

Elapsed time: 0 h 47 m 29.56 s
0


HTML(value='')

...

Exiting sweep main thread #{} via return 1400

Elapsed time: 0 h 47 m 19.94 s
0


HTML(value='')

Started at:  Oct 20 2018 05:15:23


C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


Exiting sweep main thread #{} via return 9072

Elapsed time: 0 h 47 m 18.05 s


In [35]:
rf_switch.do_set_switch(4, channel=1)
print (rf_switch.do_get_switch(channel=1))
time.sleep(900)

0


In [36]:
# Gain&noise with monochroamtic excitation

In [44]:
from qsweepy import data_reduce
pna.set_power(-50)
pna.set_nop(1000)
pna.set_span(0)
pna.set_bandwidth(1e5)

vna_std = data_reduce.data_reduce(pna)
vna_std.filters = {'S-parameter': data_reduce.mean_reducer(pna, 'S-parameter', 0),
                   'S-parameter std': data_reduce.std_reducer(pna, 'S-parameter', 0)}

#freqs = np.linspace(3.5335e9, 4.5335e9, 1001)
sweep.sweep(vna_std, (target_f, pna.set_centerfreq, 'Probe frequency', 'Hz'), \
            (target_f, p.set_target_freq_calib, 'Target frequency', 'Hz'), \
            filename='S-parameter with std -50 dBm, bw 100kHz 4e3 points')


C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


HTML(value='')

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


Started at:  Oct 20 2018 09:03:39
Waiting to join deferred threads:
Exiting sweep main thread #{} via return 4824

Elapsed time: 1 h 17 m 10.4 s


{'S-parameter': (('Probe frequency', 'Target frequency'),
  (array([5.00e+09, 5.01e+09, 5.02e+09, 5.03e+09, 5.04e+09, 5.05e+09,
          5.06e+09, 5.07e+09, 5.08e+09, 5.09e+09, 5.10e+09, 5.11e+09,
          5.12e+09, 5.13e+09, 5.14e+09, 5.15e+09, 5.16e+09, 5.17e+09,
          5.18e+09, 5.19e+09, 5.20e+09, 5.21e+09, 5.22e+09, 5.23e+09,
          5.24e+09, 5.25e+09, 5.26e+09, 5.27e+09, 5.28e+09, 5.29e+09,
          5.30e+09, 5.31e+09, 5.32e+09, 5.33e+09, 5.34e+09, 5.35e+09,
          5.36e+09, 5.37e+09, 5.38e+09, 5.39e+09, 5.40e+09, 5.41e+09,
          5.42e+09, 5.43e+09, 5.44e+09, 5.45e+09, 5.46e+09, 5.47e+09,
          5.48e+09, 5.49e+09, 5.50e+09, 5.51e+09, 5.52e+09, 5.53e+09,
          5.54e+09, 5.55e+09, 5.56e+09, 5.57e+09, 5.58e+09, 5.59e+09,
          5.60e+09, 5.61e+09, 5.62e+09, 5.63e+09, 5.64e+09, 5.65e+09,
          5.66e+09, 5.67e+09, 5.68e+09, 5.69e+09, 5.70e+09, 5.71e+09,
          5.72e+09, 5.73e+09, 5.74e+09, 5.75e+09, 5.76e+09, 5.77e+09,
          5.78e+09, 5.79e+09, 5.

In [17]:
sa.get_tracedata()

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


[array([1.00000000e+07, 3.64900000e+07, 6.29800000e+07, ...,
        2.64470200e+10, 2.64735109e+10, 2.64999997e+10]),
 array([ -37.21106339, -107.3215332 ,  -72.21500397, ...,  -54.82409668,
         -86.64167023,  -55.69965744])]

In [16]:
sa._visainstrument.write('SYST:PRES')

(11, <StatusCode.success: 0>)

In [27]:
p.set_target_freq_calib()

TypeError: load_calibration() missing 2 required positional arguments: 'path' and 'name'

# Saturation measurement

In [ ]:
probe_powers = np.linspace(-25, -0, 101)
target_frequencies = np.linspace(7.75e9, 8.25e9, 51)
pna.set_bandwidth(1e2)
pna.set_nop(1)
#pna.set_xlim(6.8e9, 8.2e9)

def set_frequency(f):
    p.set_target_freq_calib(f)
    pna.set_centerfreq(f)

sweeper.sweep(pna, 
              (probe_powers, pna.set_power, 'probe power (on VNA)', 'dBm'), 
              (target_frequencies, set_frequency, 'Target_frequency', 'Hz'),
              measurement_type='paramp_saturation_target_scan',
              references={'paramp_calibration':calibration.id})

In [17]:
sweeper.sweep(pna, measurement_type='gain_measurement', 
              references={'room_cable_calibration':4156}, 
              metadata={'bias':-0.8, 'pump_freq':})

S-parameter
load time:  0.04092240333557129
pre_trace_time:  0.0014965534210205078
trace 0 time:  0.012974739074707031
trace 1 time:  0.026948213577270508
trace 2 time:  0.04191994667053223
trace 3 time:  0.05789017677307129


start: 2019-10-26 13:29:19.460545, started/done/total sweeps: 0/1/1.0, 
Measured data: 
'S-parameter': parameters: Frequency (Hz),:[6000000000.0, 11000000000.0] (5001 points) without setter
data: [-0.06391349-0.06415067j -0.07259786-0.05444533j -0.07982449-0.04351389j
 ... -0.07445569-0.01888742j -0.07642386-0.00791384j
 -0.07675027+0.00325615j]

In [30]:
lo1.get_power()

-5.89

# bandwidth measurement

In [ ]:
probe_powers = np.linspace(-40, -15, 251)
target_frequencies = np.linspace(7.75e9, 8.25e9, 51)
pna.set_bandwidth(200)
pna.set_nop(501)
pna.set_xlim(7.5e9, 8.5e9)
pna.set_power(-40)

def set_frequency(f):
    p.set_target_freq_calib(f)

sweeper.sweep(pna, 
              #(probe_powers, pna.set_power, 'probe power (on VNA)', 'dBm'), 
              (target_frequencies, set_frequency, 'Target_frequency', 'Hz'),
              measurement_type='paramp_bandwidth_scan',
              references={'paramp_calibration':calibration.id},
              metadata={'probe_power':pna.get_power()})

# Measurement postprocessing

In [1]:
# Мощность шума
from qsweepy.paramp import *
from scipy.constants import Boltzmann, Planck
import time

#paramp = paramp(pna, lo1, current_src)
p = paramp(None, None, None)
p.set_target_f(5e9)
p.set_target_bw(1e6)
p.set_target_power(-50)
p.hint_maxfun = 50
p.pump_on = True

meas_noise = p.load_noise_measurement(((((0.86, 0.25), (0.028, 0.75)), 
            r'C:\Data\2018-10-20\04-12-57-WTJPA 31-3 Ic6.9uAC3.6pF switch 1 Still 6dB\WTJPA 31-3 Ic6.9uAC3.6pF switch 1 Still 6dB.pkl'),
                (((0.028, 1.0),), 
            r'C:\Data\2018-10-20\05-15-23-WTJPA 31-3 Ic6.9uAC3.6pF switch 2 MC\WTJPA 31-3 Ic6.9uAC3.6pF switch 2 MC.pkl')), bw=1e6)
##meas_saturation = p.load_gain_saturation_measurement(r'C:\Data\2018-10-19\17-50-42-VNA Gain Saturation\VNA Gain Saturation.pkl')

#file = open('D:\\qtlab\\ReiData\\data\\2017-06-22\\17-21-47\\Power VNA -70 dBm power on SA, bw 5e4.pkl', 'rb')
#data = pickle.load(file)
#file.close()
#paramp.attenuation = np.nanmedian(data[1]['Power'][2])-np.log10(np.nanmedian(paramp.G))*10+70
#print (paramp.attenuation)

#meas_noise_m = p.load_vna_noise_measurement(\
#                filename=r'C:\Data\2018-10-20\09-03-39-S-parameter with std -50 dBm, bw 100kHz 4e3 points\S-parameter with std -50 dBm, bw 100kHz 4e3 points.pkl', \
#                bw=5e4, atten=-70, vna_power=-50)


C:\qtlab_replacement\qsweepy\paramp.py:258: RuntimeWarning: divide by zero encountered in double_scalars
  TN = GkTNbw/(Boltzmann*G*bw)


In [2]:
%matplotlib qt5
from qsweepy import plotting
plotting.plot_measurement(meas_noise)

{'Gain frequency dependence': {'axes': <matplotlib.axes._subplots.AxesSubplot at 0x132c4954f98>,
  'plots': {'Gain frequency dependence': {'mname': 'Gain frequency dependence',
    'filter': <function qsweepy.plotting.plot_measurement.<locals>.<lambda>(x)>,
    'plot': <matplotlib.image.AxesImage at 0x132c81c0be0>}},
  'subplots': True},
 'Noise T frequency dependence': {'axes': <matplotlib.axes._subplots.AxesSubplot at 0x132c4c59d68>,
  'plots': {'Noise T frequency dependence': {'mname': 'Noise T frequency dependence',
    'filter': <function qsweepy.plotting.plot_measurement.<locals>.<lambda>(x)>,
    'plot': <matplotlib.image.AxesImage at 0x132c8b07e10>}},
  'subplots': True},
 'Gain': {'axes': <matplotlib.axes._subplots.AxesSubplot at 0x132c4c2f6d8>,
  'plots': {'Gain': {'mname': 'Gain',
    'filter': <function qsweepy.plotting.plot_measurement.<locals>.<lambda>(x)>,
    'plot': <matplotlib.lines.Line2D at 0x132c4c3b588>}},
  'subplots': True},
 'Noise T': {'axes': <matplotlib.axes

In [5]:
meas_noise_m = p.load_vna_noise_measurement(\
                filename=r'C:\Data\2018-10-20\09-03-39-S-parameter with std -50 dBm, bw 100kHz 4e3 points\S-parameter with std -50 dBm, bw 100kHz 4e3 points.pkl', \
                bw=5e4, atten=-60, vna_power=-50, transpose=True)

In [6]:
plotting.plot_measurement(meas_noise_m)

{'Monochromatic gain frequency dependence': {'axes': <matplotlib.axes._subplots.AxesSubplot at 0x132c9da14e0>,
  'plots': {'Monochromatic gain frequency dependence': {'mname': 'Monochromatic gain frequency dependence',
    'filter': <function qsweepy.plotting.plot_measurement.<locals>.<lambda>(x)>,
    'plot': <matplotlib.image.AxesImage at 0x132c9e16048>}},
  'subplots': True},
 'Monochromatic noise T frequency dependence': {'axes': <matplotlib.axes._subplots.AxesSubplot at 0x132c9df6400>,
  'plots': {'Monochromatic noise T frequency dependence': {'mname': 'Monochromatic noise T frequency dependence',
    'filter': <function qsweepy.plotting.plot_measurement.<locals>.<lambda>(x)>,
    'plot': <matplotlib.image.AxesImage at 0x132c880f7f0>}},
  'subplots': True},
 'Monochromatic gain': {'axes': <matplotlib.axes._subplots.AxesSubplot at 0x132c9dd0128>,
  'plots': {'Monochromatic gain': {'mname': 'Monochromatic gain',
    'filter': <function qsweepy.plotting.plot_measurement.<locals>.<lam

# Phase sensitive stuff

In [5]:
points_realimag = []
for i in range(10):
    points = pna.get_tracedata()
    points_realimag.extend(points[0]*np.exp(1j*points[1]))
points_realimag = np.asarray(points_realimag)

NameError: name 'pna' is not defined

In [34]:
plt.contour(h2dx, h2dy, h2dc)

TypeError: Length of x must be number of columns in z.

In [38]:
h2dc, h2dx, h2dy = np.histogram2d(np.real(points_realimag), np.imag(points_realimag), bins=100)
plt.pcolormesh(h2dx, h2dy, h2dc)
plt.axis('equal')
#h2dx, h2dy, h2dc

(-0.011852732859551907,
 0.012085455469787123,
 -0.0092373499646782875,
 0.008359985426068306)

In [48]:
plt.hist2d(np.real(points_realimag), np.imag(points_realimag), bins=100)
mu = np.mean(points_realimag)
sigma_xx = np.sum(np.real(points_realimag)*np.real(points_realimag))
sigma_xy = np.sum(np.real(points_realimag)*np.imag(points_realimag))
sigma_yy = np.sum(np.imag(points_realimag)*np.imag(points_realimag))
D,V = np.linalg.eigh([[sigma_xx, sigma_xy], [sigma_xy, sigma_yy]])
print('E[V]: ',mu, 
      '\nD[Re[V]]: ', sigma_xx, 
      '\nE[Re[V]*Im[V]]: ', sigma_xy, 
      '\nD[Im[V]]: ', sigma_yy,
      '\nD in eigenbasis:', D, 
      '\nphase:', np.arctan2(V[0][1], V[0][0])*180/np.pi)

E[V]:  (-1.09633309676e-06+4.64826868259e-07j) 
D[Re[V]]:  0.189814424429 
E[Re[V]*Im[V]]:  -0.000432359720813 
D[Im[V]]:  0.191233333437 
D in eigenbasis: [ 0.18969306  0.1913547 ] 
phase: -164.320400826


In [50]:
plt.hist2d(np.real(points_realimag), np.imag(points_realimag), bins=100)
mu = np.mean(points_realimag)
sigma_xx = np.sum(np.real(points_realimag)*np.real(points_realimag))
sigma_xy = np.sum(np.real(points_realimag)*np.imag(points_realimag))
sigma_yy = np.sum(np.imag(points_realimag)*np.imag(points_realimag))
D,V = np.linalg.eigh([[sigma_xx, sigma_xy], [sigma_xy, sigma_yy]])
print('E[V]: ',mu, 
      '\nD[Re[V]]: ', sigma_xx, 
      '\nE[Re[V]*Im[V]]: ', sigma_xy, 
      '\nD[Im[V]]: ', sigma_yy,
      '\nD in eigenbasis:', D, 
      '\nphase:', np.arctan2(V[0][1], V[0][0])*180/np.pi)

E[V]:  (-5.87944470499e-06-5.42471329467e-06j) 
D[Re[V]]:  0.426582029185 
E[Re[V]*Im[V]]:  -0.0568836338754 
D[Im[V]]:  0.305046833754 
D in eigenbasis: [ 0.28257713  0.44905174] 
phase: -111.554604256


In [55]:
plt.hist2d(np.real(points_realimag), np.imag(points_realimag), bins=100)
mu = np.mean(points_realimag)
sigma_xx = np.sum(np.real(points_realimag)*np.real(points_realimag))
sigma_xy = np.sum(np.real(points_realimag)*np.imag(points_realimag))
sigma_yy = np.sum(np.imag(points_realimag)*np.imag(points_realimag))
D,V = np.linalg.eigh([[sigma_xx, sigma_xy], [sigma_xy, sigma_yy]])
print('E[V]: ',mu, 
      '\nD[Re[V]]: ', sigma_xx, 
      '\nE[Re[V]*Im[V]]: ', sigma_xy, 
      '\nD[Im[V]]: ', sigma_yy,
      '\nD in eigenbasis:', D, 
      '\nphase:', np.arctan(V[0][1]/V[0][0])*180/np.pi)

E[V]:  (8.32477163453e-06+3.24525215766e-06j) 
D[Re[V]]:  0.279407294951 
E[Re[V]*Im[V]]:  -0.00358029796172 
D[Im[V]]:  0.452435764483 
D in eigenbasis: [ 0.27933324  0.45250982] 
phase: 1.18488579427


In [7]:
# векторный анализатор в режим линейного свипа
pna.set_sweep_mode("LIN")

True

In [59]:
phases = np.linspace(-np.pi, np.pi, 361)
pna.set_xlim(4.0335e9, 4.0335e9)
sweep.sweep(pna, (phases, lo1.set_phase, 'Pump phase'), filename='Phase-sensitive noise amplification')

A Jupyter Widget

Started at:  May 04 2018 19:49:13


C:\ProgramData\Anaconda3\lib\site-packages\matplotlib\axes\_base.py:3285: UserWarning: Attempting to set identical bottom==top results
in singular transformations; automatically expanding.
bottom=4033500000.0, top=4033500000.0
  'bottom=%s, top=%s') % (bottom, top))



Elapsed time: 0 h 20 m 8.94 s


{'S-parameter': (('Pump phase', 'Frequency'),
  (array([-3.14159265, -3.12413936, -3.10668607, -3.08923278, -3.07177948,
          -3.05432619, -3.0368729 , -3.01941961, -3.00196631, -2.98451302,
          -2.96705973, -2.94960644, -2.93215314, -2.91469985, -2.89724656,
          -2.87979327, -2.86233997, -2.84488668, -2.82743339, -2.8099801 ,
          -2.7925268 , -2.77507351, -2.75762022, -2.74016693, -2.72271363,
          -2.70526034, -2.68780705, -2.67035376, -2.65290046, -2.63544717,
          -2.61799388, -2.60054059, -2.58308729, -2.565634  , -2.54818071,
          -2.53072742, -2.51327412, -2.49582083, -2.47836754, -2.46091425,
          -2.44346095, -2.42600766, -2.40855437, -2.39110108, -2.37364778,
          -2.35619449, -2.3387412 , -2.32128791, -2.30383461, -2.28638132,
          -2.26892803, -2.25147474, -2.23402144, -2.21656815, -2.19911486,
          -2.18166156, -2.16420827, -2.14675498, -2.12930169, -2.11184839,
          -2.0943951 , -2.07694181, -2.05948852, -2.04

# Spectroscopy

In [14]:
current_src.set_current(7.4e-3)

True

In [19]:
lo1.set_status(1)
lo1.set_frequency(4.70805e9)
power=np.linspace(-20,-10,21)
pna.set_xlim(4.6e9,4.62e9)
sweep.sweep(pna,(power,lo1.set_power,"Pump Power","dBm"),filename="Paramp pupm power sweep")

Started at:  Nov 16 2017 15:48:19

Elapsed time: 0 h 0 m 37.85 s


{'S-parameter': (('Pump Power', 'Frequency'),
  (array([-20. , -19.5, -19. , -18.5, -18. , -17.5, -17. , -16.5, -16. ,
          -15.5, -15. , -14.5, -14. , -13.5, -13. , -12.5, -12. , -11.5,
          -11. , -10.5, -10. ]),
   array([  4.60000000e+09,   4.60006667e+09,   4.60013333e+09,
            4.60020000e+09,   4.60026667e+09,   4.60033333e+09,
            4.60040000e+09,   4.60046667e+09,   4.60053333e+09,
            4.60060000e+09,   4.60066667e+09,   4.60073333e+09,
            4.60080000e+09,   4.60086667e+09,   4.60093333e+09,
            4.60100000e+09,   4.60106667e+09,   4.60113333e+09,
            4.60120000e+09,   4.60126667e+09,   4.60133333e+09,
            4.60140000e+09,   4.60146667e+09,   4.60153333e+09,
            4.60160000e+09,   4.60166667e+09,   4.60173333e+09,
            4.60180000e+09,   4.60186667e+09,   4.60193333e+09,
            4.60200000e+09,   4.60206667e+09,   4.60213333e+09,
            4.60220000e+09,   4.60226667e+09,   4.60233333e+09,
       

## Резонаторная спектроскопия

In [7]:
pna.set_timeout(30000)
pna.set_trigger_source("MAN")
pna.init()
pna.ask("*OPC?")
pna.get_tracedata()
pna.set_trigger_source("IMM")

res_data = pna.get_tracedata()
res_freqs = pna.get_freqpoints()
plt.figure("S21_amp")
plt.plot(res_freqs, res_data[0])
plt.figure("S21_ph")
plt.plot(res_freqs, res_data[1])


In [35]:
plt.figure("S21_amp")
plt.plot(res_freqs, 20.*np.log10(res_data[0]))
plt.figure("S21_ph")
plt.plot(res_freqs, res_data[1])

In [11]:
save_pkl({'type':"gain",}, {"Amp": res_data[0] , "Ph": res_data[1], "freqs": res_freqs } ,plot=False)

In [29]:
pna.set_xlim(6.58e9, 6.59e9)
pna.set_bandwidth(1e1)
pna.set_nop(201)
pna.set_power(-60)

True

In [10]:
pna.set_xlim(7.3e9,9.5e9)
pna.set_nop(600)

True

In [11]:
currents = np.linspace(-10e-3, 10e-3, 400)
current_src.set_voltage_compliance(20)
current_src.set_range(10e-3)
current_src.set_status(1)

True

In [61]:
pna.set_bandwidth(100)
powers = np.arange(-80,-45,1.)
sweep.sweep(pna, (powers, pna.set_power, 'PNA power'), filename='Gain')

A Jupyter Widget

Started at:  May 04 2018 21:03:18

Elapsed time: 0 h 5 m 28.26 s


{'S-parameter': (('PNA power', 'Frequency'),
  (array([-80., -79., -78., -77., -76., -75., -74., -73., -72., -71., -70.,
          -69., -68., -67., -66., -65., -64., -63., -62., -61., -60., -59.,
          -58., -57., -56., -55., -54., -53., -52., -51., -50., -49., -48.,
          -47., -46.]),
   array([  3.53350000e+09,   3.53450000e+09,   3.53550000e+09, ...,
            4.53150000e+09,   4.53250000e+09,   4.53350000e+09])),
  array([[-1.72948015-1.02590764j, -1.60714936-0.87781173j,
          -1.80276310-0.18702404j, ...,  0.01107773+7.66779661j,
           2.13911486+6.74586105j,  4.55912161+5.43679953j],
         [-1.43331325-1.19634759j, -1.44471133-0.73747236j,
          -2.11441064+0.17149197j, ...,  0.33157068+7.00325537j,
           2.56824303+6.70178509j,  4.70737600+5.63263369j],
         [-1.32487130-1.30654323j, -1.57349193-0.85744679j,
          -1.88826609-0.30985233j, ...,  0.23080876+7.34466076j,
           2.32970119+6.90654612j,  4.50229883+5.71517181j],
         

In [10]:
lo1.set_frequency(8.74e9)
lo1.set_status(1)

True

In [ ]:
ex_powers = np.arange(8,18,0.01)
pna.set_centerfreq(4.37e9)
pna.set_span(2000e6)
pna.set_nop(201)
pna.set_bandwidth(100)
pna.set_power(-60)
sweep.sweep(pna, (ex_powers, lo1.set_power, 'excitation power'), filename='WTJPA Ic6.9uAC3.6pF ex8.74GHz')

In [7]:
lo1.set_status(0)

True

# Усиление при разных мощностях накачки

In [11]:
pump_powers = np.linspace(-5, 4, 90)
probe_freq_start = pna.get_startfreq()#8.6189e9
probe_freq_end = pna.get_stopfreq()#['S-paramater']8.6689e9

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


In [13]:
sweep.sweep(pna, (pump_powers, lo1.set_power, 'excitation power', 'dBm'), filename='WTJPA Ic6.9uAC3.6pF ex7GHz')

HTML(value='')

Started at:  Oct 16 2018 07:59:38


C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


Exiting sweep main thread #{} via return 12208

Elapsed time: 0 h 3 m 15.69 s


{'S-parameter': (('excitation power', 'Frequency'),
  (array([-5.        , -4.8988764 , -4.79775281, -4.69662921, -4.59550562,
          -4.49438202, -4.39325843, -4.29213483, -4.19101124, -4.08988764,
          -3.98876404, -3.88764045, -3.78651685, -3.68539326, -3.58426966,
          -3.48314607, -3.38202247, -3.28089888, -3.17977528, -3.07865169,
          -2.97752809, -2.87640449, -2.7752809 , -2.6741573 , -2.57303371,
          -2.47191011, -2.37078652, -2.26966292, -2.16853933, -2.06741573,
          -1.96629213, -1.86516854, -1.76404494, -1.66292135, -1.56179775,
          -1.46067416, -1.35955056, -1.25842697, -1.15730337, -1.05617978,
          -0.95505618, -0.85393258, -0.75280899, -0.65168539, -0.5505618 ,
          -0.4494382 , -0.34831461, -0.24719101, -0.14606742, -0.04494382,
           0.05617978,  0.15730337,  0.25842697,  0.35955056,  0.46067416,
           0.56179775,  0.66292135,  0.76404494,  0.86516854,  0.96629213,
           1.06741573,  1.16853933,  1.26966292,

# Измерение усиления и шумов

In [10]:
# Мощность шума
from qsweepy.paramp import *

In [11]:
from scipy.constants import Boltzmann, Planck
import time
sw_ch = 1
T1_sw = 4
T2_sw = 2
T1_Ts = [0.028]
T1_gains = [1]
T2_Ts = [0.028, 0.87]
T2_gains = [0.749, 0.251]
bw = 1e3



In [13]:
planck_function(8.6e9, T1_Ts, T1_gains)*3e3

NameError: name 'planck_function' is not defined

In [18]:
pump_powers = np.linspace(-7, -4, 301)
probe_freq_start = pna.get_startfreq()#8.6189e9
probe_freq_end = pna.get_stopfreq()#['S-paramater']8.6689e9
rbw = 1e5
vbw = 100

sa.set_xlim(probe_freq_start, probe_freq_end)
sa.set_detector('rms')
sa.set_res_bw(rbw)
sa.set_video_bw(vbw)
#sa.set_ref(-20)
#current_src.set_current(62.6e-6)

True

In [5]:
m = sa.measure()
plt.plot(sa.get_freqpoints(), m['Power'])

In [4]:
m1=m

In [13]:
plt.plot(sa.get_freqpoints(), m['Power'])
plt.plot(sa.get_freqpoints(),m1["Power"])

In [12]:
save_pkl({"type":"noize"}, {"Cold":m1, "Hot":m, "F":sa.get_freqpoints(), "comment":"hot - 3.5K through 6 dB"},plot=False)

In [24]:
sa.set_xlim(6.5e9, 8e9)

In [30]:
time.sleep(240)
pna.set_status(False)
lo1.set_status(True)
m_cold_on = sweep.sweep(sa, ([0], lambda x: 0, 'Dummy'), filename='Paramp cold off terminated noise')#sa.measure()
lo1.set_status(False)
#plt.plot(sa.get_freqpoints(), m['Power'])
m_cold_off = sweep.sweep(sa, ([0], lambda x: 0, 'Dummy'), filename='Paramp cold on terminated noise')#sa.measure()
lo1.set_status(True)
#plt.plot(sa.get_freqpoints(), m['Power'])
pna.set_status(False)

Started at:  Jan 17 2018 19:20:01

Elapsed time: 0 h 3 m 55.06 s


Started at:  Jan 17 2018 19:23:56

Elapsed time: 0 h 3 m 55.2 s


True

In [31]:
time.sleep(240)
pna.set_status(False)
lo1.set_status(True)
m_hot_on = sweep.sweep(sa, ([0], lambda x: 0, 'Dummy'), filename='Paramp hot off terminated noise')#sa.measure()
lo1.set_status(False)
#plt.plot(sa.get_freqpoints(), m['Power'])
m_hot_off = sweep.sweep(sa, ([0], lambda x: 0, 'Dummy'), filename='Paramp hot on terminated noise')#sa.measure()
lo1.set_status(True)
#plt.plot(sa.get_freqpoints(), m['Power'])
pna.set_status(False)

Started at:  Jan 17 2018 19:38:58

Elapsed time: 0 h 3 m 54.9 s


Started at:  Jan 17 2018 19:42:54

Elapsed time: 0 h 3 m 54.91 s


True

In [59]:
sa.measure()

{'Power': array([-81.37501526, -81.62197113, -81.65299225, ..., -83.43331146,
        -83.43353271, -83.41014099])}

In [33]:
p = paramp(pna, lo1, current_src);

In [43]:
Gain, Noise = p.gain_noise(m_cold_on['Power'][1][0], [10**(m_cold_on['Power'][2]/10), 10**(m_hot_on['Power'][2]/10)], [[27e-3, 1.0]], [[3.387, 0.1], [27e-3, 0.9]], 1e6)

In [58]:
probe_powers = np.linspace(-70, -35, 36);
nop = 1501
pna.set_nop(nop)
pna.set_bandwidth(100)
time.sleep(240)
sweep.sweep(pna, (probe_powers, pna.set_power, 'Probe signal strength'), filename='Paramp (WTJPA) saturation')

Started at:  Jan 17 2018 20:21:36

Elapsed time: 0 h 8 m 29.04 s


{'S-parameter': (('Probe signal strength', 'Frequency'),
  (array([-70., -69., -68., -67., -66., -65., -64., -63., -62., -61., -60.,
          -59., -58., -57., -56., -55., -54., -53., -52., -51., -50., -49.,
          -48., -47., -46., -45., -44., -43., -42., -41., -40., -39., -38.,
          -37., -36., -35.]),
   array([  6.50000000e+09,   6.50100000e+09,   6.50200000e+09, ...,
            7.99800000e+09,   7.99900000e+09,   8.00000000e+09])),
  array([[-0.04686300+0.02887802j, -0.03115846+0.04496023j,
          -0.01973630+0.05004913j, ..., -0.04084054-0.00918119j,
          -0.04100863+0.00498566j, -0.04702640+0.01599258j],
         [-0.04465297+0.03138864j, -0.03196773+0.03647516j,
          -0.01609762+0.04998083j, ..., -0.04568706-0.00502704j,
          -0.05727162+0.00874494j, -0.03469763+0.01050992j],
         [-0.03793304+0.02805062j, -0.02649711+0.04497258j,
          -0.01273276+0.04524743j, ..., -0.04268286-0.0102803j ,
          -0.03786205+0.00089701j, -0.03860448+0.012

In [39]:
plt.figure()
plt.plot(m_cold_on['Power'][1][0], m_cold_on['Power'][2], label='cold')
plt.plot(m_cold_on['Power'][1][0], m_hot_on['Power'][2], label='hot')
plt.legend()

In [54]:
from scipy.constants import h, k
plt.figure()
plt.plot(m_cold_on['Power'][1][0]/1e9, Noise)
plt.ylim([0, 5])
plt.plot(m_cold_on['Power'][1][0]/1e9, m_cold_on['Power'][1][0]*h/k*0.5, linestyle=':')
plt.xlim([6.6, 8])
plt.grid()
plt.xlabel('Frequency, GHz')
plt.ylabel('Noise temperature, K')

In [57]:
from scipy.constants import h, k
plt.figure()
plt.plot(m_cold_on['Power'][1][0]/1e9, np.log10(Gain)*10)
#plt.ylim([0, 5])
#plt.plot(m_cold_on['Power'][1][0]/1e9, m_cold_on['Power'][1][0]*h/k*0.5, linestyle=':')
plt.xlim([6.6, 8])
plt.grid()
plt.xlabel('Frequency, GHz')
plt.ylabel('Full system gain, dB')

c:\python36\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning: invalid value encountered in log10
  This is separate from the ipykernel package so we can avoid doing imports until


In [ ]:
save_pkl({"type":"noize"}, {"Cold":m_cold_off, "Hot":m_cold_on, "F":sa.get_freqpoints(), "comment":"hot - 3.5K through 6 dB"},plot=False)

In [21]:
noises = []
pump_freq = lo1.get_frequency()
noises.append(sweep.sweep(sa,  \
                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1 Still 6dB'.format(pump_freq/1e9)))

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


HTML(value='')

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


Started at:  Oct 16 2018 11:13:46
Exiting sweep main thread #{} via return 10184

Elapsed time: 0 h 0 m 23.05 s


In [103]:
plt.plot(m['Power'])

In [ ]:
pump_freq = lo1.get_frequency()
lo1.set_status(False)

noises = []
sa.set_bandwidth(1000e3)
sa.set_bandwidth_video(10)
sa.set_nop(1001)
sw_ch=1
pna.set_power(-95)
#rf_switch.do_set_switch(1, channel=sw_ch)
#time.sleep(120)
#noises.append(sweep.sweep(sa, (pump_powers[0:1], lo1.set_power, 'Excitation power'), \
#                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1'.format(pump_freq/1e9)))
lo1.set_status(True)

#rf_switch.do_set_switch(1, channel=sw_ch)
#print (rf_switch.do_get_switch(channel=sw_ch))
#time.sleep(600)
#noises.append(sweep.sweep(sa, (pump_powers, lo1.set_power, 'Excitation power'), \
#                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1'.format(pump_freq/1e9)))

rf_switch.do_set_switch(1, channel=sw_ch)
print (rf_switch.do_get_switch(channel=sw_ch))
time.sleep(900)
#noises.append(sweep.sweep(sa, (pump_powers, lo1.set_power, 'Excitation power'), \
#                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1 Still 6dB'.format(pump_freq/1e9)))
noises.append(sweep.sweep(sa,  \
                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1 Still 6dB'.format(pump_freq/1e9)))

rf_switch.do_set_switch(2, channel=sw_ch)
print (rf_switch.do_get_switch(channel=sw_ch))
time.sleep(900)
noises.append(sweep.sweep(sa, \
                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 2 MC'.format(pump_freq/1e9)))

rf_switch.do_set_switch(4, channel=sw_ch)
print (rf_switch.do_get_switch(channel=sw_ch))
time.sleep(900)
#noises.append(sweep.sweep(sa, (pump_powers, lo1.set_power, 'Excitation power'), \
#                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1 Still 6dB'.format(pump_freq/1e9)))
noises.append(sweep.sweep(sa,  \
                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 4 '.format(pump_freq/1e9)))

rf_switch.do_set_switch(5, channel=sw_ch)
print (rf_switch.do_get_switch(channel=sw_ch))
time.sleep(900)
noises.append(sweep.sweep(sa, \
                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 5'.format(pump_freq/1e9)))

#rf_switch.do_set_switch(5, channel=sw_ch)
#print (rf_switch.do_get_switch(channel=sw_ch))
#time.sleep(600)
#noises.append(sweep.sweep(sa, (pump_powers, lo1.set_power, 'Excitation power'), \
#                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 5'.format(pump_freq/1e9)))

C:\ProgramData\Anaconda3\lib\site-packages\pyvisa\resources\messagebased.py:573: FutureWarning: ask is deprecated and will be removed in 1.10, use query instead.
  '1.10, use query instead.', FutureWarning)


0


In [160]:
from scipy.signal import gaussian, convolve
gains = np.zeros_like(noises[1]['Power'][2])
noise_Ts = np.zeros_like(noises[1]['Power'][2])
filt = gaussian(300, 50)
filt = filt/np.sum(filt)
for power_id, pump_power in enumerate(pump_powers):
    gain, noise_T = gain_noise(noises[1]['Power'][1][1], [convolve(n['Power'][2][power_id,:], filt, mode='same') for n in [noises[3], noises[2]]])
    gains[power_id, :] = gain
    noise_Ts[power_id, :] = noise_T

[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.07239815e-13   1.11955825e-13] [  1.04169888e-13   3.58344557e+05]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.08949934e-13   1.13749911e-13] [  1.05825349e-13   3.64724695e+05]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.10659498e-13   1.15543607e-13] [  1.07480146e-13   3.71117487e+05]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.12367693e-13   1.17335751e-13] [  1.09133694e-13   3.77496310e+05]
[[  1.00000000e+00   8.56697031e-21]
 [  1.00000000e+00   2.17275175e-20]] [  1.14073416e-13   1.19125524e-13] [  1.10784703e-13   3.83882850e+05]
[[  1.00000000e+00   8.56697079e-21]
 [  1.00000000e+00   2.17275179e-20]] [  1.15775705e-13   1.20912702e-13] [  1.12431734e-13   3.90333049e+05]
[[  1.00000000e+00   8.56697126e-21]
 [  1.00000000e+00   2.17275183e-20]] [  1.17474126e-13   1.22697224e-13] [  1.14

[[  1.00000000e+00   8.56697220e-21]
 [  1.00000000e+00   2.17275192e-20]] [  1.20478375e-13   1.28300234e-13] [  1.15386668e-13   5.94341465e+05]
[[  1.00000000e+00   8.56697267e-21]
 [  1.00000000e+00   2.17275196e-20]] [  1.22186856e-13   1.30084069e-13] [  1.17046097e-13   6.00067196e+05]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.07861076e-13   1.13348591e-13] [  1.04288933e-13   4.16967051e+05]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.09569690e-13   1.15194078e-13] [  1.05908447e-13   4.27367341e+05]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.11277695e-13   1.17040229e-13] [  1.07526524e-13   4.37864354e+05]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.12984913e-13   1.18886226e-13] [  1.09143403e-13   4.48409419e+05]
[[  1.00000000e+00   8.56697031e-21]
 [  1.00000000e+00   2.17275175e-20]] [  1.14690662e-13   1.20730978e-13] [  1.10

 [  1.00000000e+00   2.17275187e-20]] [  1.17697812e-13   1.23573039e-13] [  1.13873282e-13   4.46427303e+05]
[[  1.00000000e+00   8.56697220e-21]
 [  1.00000000e+00   2.17275192e-20]] [  1.19380129e-13   1.25336892e-13] [  1.15502523e-13   4.52622760e+05]
[[  1.00000000e+00   8.56697267e-21]
 [  1.00000000e+00   2.17275196e-20]] [  1.21057325e-13   1.27094685e-13] [  1.17127252e-13   4.58746962e+05]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.05296724e-13   1.12800418e-13] [  1.00412132e-13   5.70165789e+05]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.06984338e-13   1.14583903e-13] [  1.02037338e-13   5.77450493e+05]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.08671995e-13   1.16365278e-13] [  1.03663988e-13   5.84571663e+05]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.10359316e-13   1.18144152e-13] [  1.05291711e-13   5.91528309e+05]
[[  1.00

 [  1.00000000e+00   2.17275196e-20]] [  1.21838477e-13   1.32920548e-13] [  1.14624506e-13   8.42067647e+05]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.07147698e-13   1.16289149e-13] [  1.01196994e-13   6.94610256e+05]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.08852256e-13   1.18133317e-13] [  1.02810671e-13   7.05218454e+05]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.10556257e-13   1.19976751e-13] [  1.04423906e-13   7.15813291e+05]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.12259189e-13   1.21818513e-13] [  1.06036466e-13   7.26362208e+05]
[[  1.00000000e+00   8.56697031e-21]
 [  1.00000000e+00   2.17275175e-20]] [  1.13960490e-13   1.23657528e-13] [  1.07648120e-13   7.36826363e+05]
[[  1.00000000e+00   8.56697079e-21]
 [  1.00000000e+00   2.17275179e-20]] [  1.15659491e-13   1.25492740e-13] [  1.09258453e-13   7.47176292e+05]
[[  1.00

 [  1.00000000e+00   2.17275187e-20]] [  1.15970075e-13   1.28818992e-13] [  1.07605962e-13   9.76320832e+05]
[[  1.00000000e+00   8.56697220e-21]
 [  1.00000000e+00   2.17275192e-20]] [  1.17629929e-13   1.30649155e-13] [  1.09154951e-13   9.89261795e+05]
[[  1.00000000e+00   8.56697267e-21]
 [  1.00000000e+00   2.17275196e-20]] [  1.19284362e-13   1.32473152e-13] [  1.10699004e-13   1.00214608e+06]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.02960481e-13   1.14810530e-13] [  9.52465922e-14   9.00422202e+05]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.04626277e-13   1.16647671e-13] [  9.68008489e-14   9.13441844e+05]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.06292039e-13   1.18483466e-13] [  9.83559265e-14   9.26361710e+05]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.07956793e-13   1.20317496e-13] [  9.99104881e-14   9.39224114e+05]
[[  1.00

...

 [  1.00000000e+00   2.17275192e-20]] [  1.49378326e-13   1.66755724e-13] [  1.38066358e-13   1.32041610e+06]
[[  1.00000000e+00   8.56697267e-21]
 [  1.00000000e+00   2.17275196e-20]] [  1.51483183e-13   1.69066532e-13] [  1.40037149e-13   1.33606524e+06]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.34280903e-13   1.47035543e-13] [  1.25978163e-13   9.69157284e+05]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.36413084e-13   1.49403319e-13] [  1.27956982e-13   9.87058838e+05]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.38544375e-13   1.51770186e-13] [  1.29934922e-13   1.00495903e+06]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.40674152e-13   1.54135577e-13] [  1.31911322e-13   1.02286215e+06]
[[  1.00000000e+00   8.56697031e-21]
 [  1.00000000e+00   2.17275175e-20]] [  1.42801247e-13   1.56499024e-13] [  1.33884562e-13   1.04082128e+06]
[[  1.00

 [  1.00000000e+00   2.17275187e-20]] [  1.47217299e-13   1.61807587e-13] [  1.37719625e-13   1.10863839e+06]
[[  1.00000000e+00   8.56697220e-21]
 [  1.00000000e+00   2.17275192e-20]] [  1.49298008e-13   1.64093210e-13] [  1.39666943e-13   1.12420877e+06]
[[  1.00000000e+00   8.56697267e-21]
 [  1.00000000e+00   2.17275196e-20]] [  1.51372316e-13   1.66370783e-13] [  1.41608933e-13   1.13965378e+06]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.25426958e-13   1.46294611e-13] [  1.11842984e-13   1.58562200e+06]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.27464419e-13   1.48601341e-13] [  1.13705162e-13   1.60608230e+06]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.29502769e-13   1.50906817e-13] [  1.15569624e-13   1.62637977e+06]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.31540626e-13   1.53210169e-13] [  1.17434653e-13   1.64655332e+06]
[[  1.00

 [  1.00000000e+00   2.17275196e-20]] [  1.51980606e-13   1.59676239e-13] [  1.46971066e-13   5.84750270e+05]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.30102739e-13   1.41743924e-13] [  1.22524811e-13   8.84551782e+05]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.32194156e-13   1.43982411e-13] [  1.24520492e-13   8.95726844e+05]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.34285591e-13   1.46219956e-13] [  1.26516815e-13   9.06828953e+05]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.36375738e-13   1.48455903e-13] [  1.28512053e-13   9.17907449e+05]
[[  1.00000000e+00   8.56697031e-21]
 [  1.00000000e+00   2.17275175e-20]] [  1.38463272e-13   1.50689323e-13] [  1.30504620e-13   9.28992606e+05]
[[  1.00000000e+00   8.56697079e-21]
 [  1.00000000e+00   2.17275179e-20]] [  1.40547147e-13   1.52919033e-13] [  1.32493562e-13   9.40073861e+05]
[[  1.00

 [  1.00000000e+00   2.17275192e-20]] [  1.45238296e-13   1.58175997e-13] [  1.36816387e-13   9.83067133e+05]
[[  1.00000000e+00   8.56697267e-21]
 [  1.00000000e+00   2.17275196e-20]] [  1.47331029e-13   1.60403161e-13] [  1.38821612e-13   9.93281782e+05]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.31970188e-13   1.41351007e-13] [  1.25863666e-13   7.12798499e+05]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.34093896e-13   1.43633400e-13] [  1.27884075e-13   7.24856182e+05]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.36217051e-13   1.45915675e-13] [  1.29903650e-13   7.36946885e+05]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.38338562e-13   1.48197230e-13] [  1.31920979e-13   7.49107720e+05]
[[  1.00000000e+00   8.56697031e-21]
 [  1.00000000e+00   2.17275175e-20]] [  1.40457448e-13   1.50476980e-13] [  1.33935149e-13   7.61330932e+05]
[[  1.00

 [  1.00000000e+00   2.17275192e-20]] [  1.46947832e-13   1.59508362e-13] [  1.38771447e-13   9.54407858e+05]
[[  1.00000000e+00   8.56697267e-21]
 [  1.00000000e+00   2.17275196e-20]] [  1.49008853e-13   1.61718519e-13] [  1.40735385e-13   9.65739964e+05]
[[  1.00000000e+00   8.56696843e-21]
 [  1.00000000e+00   2.17275158e-20]] [  1.26670546e-13   1.39940633e-13] [  1.18032271e-13   1.00832334e+06]
[[  1.00000000e+00   8.56696890e-21]
 [  1.00000000e+00   2.17275162e-20]] [  1.28710332e-13   1.42147457e-13] [  1.19963323e-13   1.02101567e+06]
[[  1.00000000e+00   8.56696937e-21]
 [  1.00000000e+00   2.17275166e-20]] [  1.30749378e-13   1.44350301e-13] [  1.21895742e-13   1.03346185e+06]
[[  1.00000000e+00   8.56696984e-21]
 [  1.00000000e+00   2.17275170e-20]] [  1.32787359e-13   1.46548682e-13] [  1.23829309e-13   1.04564974e+06]
[[  1.00000000e+00   8.56697031e-21]
 [  1.00000000e+00   2.17275175e-20]] [  1.34823862e-13   1.48742200e-13] [  1.25763602e-13   1.05758050e+06]
[[  1.00

In [161]:
header = {'name':'JPA Ic6.9uA res', 'type':'Noise & Gain', 'params':['Pump power', 'Probe frequency']}
save_pkl(header, {'Gain':(noises[1]['Power'][0], noises[1]['Power'][1], gains, noises[1]['Power'][3]),
          'Noise Temp':(noises[1]['Power'][0], noises[1]['Power'][1], noise_Ts, {'log':False})})

c:\python36\lib\site-packages\matplotlib\backend_bases.py:2445: MatplotlibDeprecationWarning: Using default event loop until function specific to this GUI is implemented
  warnings.warn(str, mplDeprecation)


In [166]:
axes = plt.gca()
image = axes.get_images()[0]
image.set_clim(0, 2)

In [90]:
np.linalg.lstsq([[1, 1e-20], [1, 2e-20]], [1e-10, 1.1e-10])

(array([  1.05000000e-10,   1.57500000e-30]),
 array([], dtype=float64),
 1,
 array([  1.41421356e+00,   7.07106781e-21]))

In [ ]:
nois

In [57]:
from scipy.signal import medfilt
plt.figure(figsize=(12,8))
cross_sections = [130, 140, 150, 160]
for cs in cross_sections:
    noise_Ts_filtered = noise_Ts[2][cs,:]
    noise_Ts_filtered[noise_Ts_filtered<0] = np.nan
    noise_Ts_filtered[noise_Ts_filtered>6] = np.nan
    noise_Ts_filtered_freqs = noise_Ts[1][1][np.isfinite(noise_Ts_filtered)]
    plt.scatter(noise_Ts_filtered_freqs, medfilt(noise_Ts_filtered[np.isfinite(noise_Ts_filtered)], 9), s=4, label='{0} dBm'.format(noise_Ts[1][0][cs]))
    
plt.title('Added noise temperature')
plt.xlabel('Frequency, Hz')
plt.ylabel('Temperature, K')
plt.grid(True)
plt.legend()

c:\python36\lib\site-packages\ipykernel_launcher.py:6: RuntimeWarning: invalid value encountered in less
  
c:\python36\lib\site-packages\ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in greater
  import sys


In [63]:
from scipy.signal import medfilt
plt.figure(figsize=(12,8))
cross_sections = [130, 140, 150, 160]
for cs in cross_sections:
    gains_filtered = gains[2][cs,:]
    gains_filtered[gains_filtered<0] = np.nan
    #gains_filtered[noise_Ts_filtered>6] = np.nan
    gains_filtered_freqs = noise_Ts[1][1][np.isfinite(gains_filtered)]
    plt.scatter(gains_filtered_freqs, 10*np.log10(gains_filtered[np.isfinite(gains_filtered)]), s=4, label='{0} dBm'.format(noise_Ts[1][0][cs]))
    
plt.title('Gain')
plt.xlabel('Frequency, Hz')
plt.ylabel('Gain, dB')
plt.grid(True)
plt.legend()

In [ ]:
plt.figure(figsize=(12,8))
plt.plot(noises[1]['Power'][1][1], np.log10(noises[1]['Power'][2][150,:])*10, label='40mK')
plt.plot(noises[2]['Power'][1][1], np.log10(noises[2]['Power'][2][150,:])*10, label='3.42K (10 dB)')
plt.title('Noise Power (pump power {0} dBm)'.format(noises[1]['Power'][1][0][150]))
plt.xlabel('Frequency, Hz')
plt.ylabel('Power, dBm')

In [17]:
class paramp:
    def __init__(self, vna, pump_src, bias_src):
        self.vna = vna
        self.pump_src = pump_src
        self.bias_src = bias_src
        self.optimal_points = {}
        
        self.target_f = None
        self.target_bw = None
        self.target_power = None
        
        self.hint_fp_offset = 100e6
        self.hint_rel_errors = (1e-4, 1e-2, 1e-2)
        self.hint_maxfun = 200
        self.hint_nop = 5000
        self.hint_span_bw = 30.
        
        self.pump_on = True

    def measure(self):
    # maximize SNR of S21 at given frequency, excitation power and bandwidth
        pna.set_nop(self.hint_nop)
        pna.set_bandwidth(self.target_bw)
        pna.set_power(self.target_power)
        pna.set_centerfreq(self.target_f)
        pna.set_span(self.target_bw/self.hint_span_bw)
    
        params = ((self.pump_src.set_frequency, self.pump_src.get_frequency()),
                  (self.pump_src.set_power, self.pump_src.get_power()),
                  (self.bias_src.set_current, self.bias_src.get_current()))
        initial_simplex=[[p[1]*(1+self.hint_rel_errors[p_id]) if v==p_id else p[1] for p_id,p in enumerate(params)] for v in range(len(params)+1)]
        self.pump_src.set_status(self.pump_on)
        self.bias_src.set_status(True)
    
        def target():
            time.sleep(0.4)
            measurements = pna.measure()['S-parameter'].ravel()
            print (np.log10(np.abs(np.mean(measurements)))*20, np.log10(np.std(measurements)/np.abs(np.mean(measurements)))*10)
            return np.std(measurements)/np.abs(np.mean(measurements))
    
        res = sweep.optimize(target, *params, initial_simplex = initial_simplex, maxfun=self.hint_maxfun)
        for x, p in zip(res[0], params): p[0](x)
        S21 = pna.measure()['S-parameter'].ravel()[0]
        measurement = {'S-parameter':np.asarray(S21), 
                       'SNR':np.asarray(res[1]), 
                       'Pump frequency':np.asarray(res[0][0]), 
                       'Pump power': np.asarray(res[0][1]), 
                       'Bias': np.asarray(res[0][2])}
        return measurement
    
    def set_target_f(self, value):
        self.target_f = value
    
    def set_target_bw(self, value):
        self.target_bw = value
        
    def set_target_power(self, value):
        self.target_power = value
    
    def get_opts(self):
        return {'S-parameter':{'log':20}, 
                'SNR':{'log':20}, 
                'Pump frequency':{'log':False}, 
                'Pump power':{'log':False}, 
                'Bias':{'log':False}}
    
    def get_points(self):
        return {'S-parameter':[],
                'SNR':[], 
                'Pump frequency':[], 
                'Pump power':[], 
                'Bias':[]}
    
    def get_dtype(self):
        return {'S-parameter':np.complex,
                'SNR':np.float, 
                'Pump frequency':np.float, 
                'Pump power':np.float, 
                'Bias':np.float}
                  
    def set_parameters(self, f, power, bias):
        import time
        params = self.measure()
        pump_src.set_frequency(params['Pump frequency'])
        pump_src.set_power(params['Pump power'])
        bias_src.set_current(params['Bias'])
        
    def load_calibration(self, path, name):
        import pickle
        from scipy.interpolate import interp1d
        bias_name = 'Bias Paramp VNA calib'
        pumpfreq_name = 'Pump frequency Paramp VNA calib'
        pumppower_name = 'Pump power Paramp VNA calib'
        self.calib_bias = pickle.load(open('{0}\\{1} {2}.pkl'.format(path, bias_name, name), 'rb'))[1]['Bias'][2]
        self.calib_pumpfreq = pickle.load(open('{0}\\{1} {2}.pkl'.format(path, pumpfreq_name, name), 'rb'))[1]['Pump frequency'][2]
        self.calib_pumppower = pickle.load(open('{0}\\{1} {2}.pkl'.format(path, pumppower_name, name), 'rb'))[1]['Pump power'][2]
        self.calib_targetfreq = pickle.load(open('{0}\\{1} {2}.pkl'.format(path, pumppower_name, name), 'rb'))[1]['Pump power'][1][0]
        self.pump_frequency_by_target_frequency = interp1d(self.calib_targetfreq, self.calib_pumpfreq)
        self.pump_power_by_target_frequency = interp1d(self.calib_targetfreq, self.calib_pumppower)
        self.bias_by_target_frequency = interp1d(self.calib_targetfreq, self.calib_bias)
    
    def load_noise_measurement(self, temp_files, bw):
        import pickle
        self.GN_P = []
        for T, f in temp_files:
            noise_powers = pickle.load(open(f, 'rb'))[1]['Power']
            self.GN_target_frequencies = noise_powers[1][0]
            self.GN_frequencies = noise_powers[1][1]
            self.GN_P.append(10**(noise_powers[2]/10))
        self.G = np.zeros_like(self.GN_P[0])
        self.TN = np.zeros_like(self.GN_P[0])
        self.G_1d = np.zeros(self.GN_target_frequencies.shape[0])
        self.TN_1d = np.zeros(self.GN_target_frequencies.shape[0])
        for tf_id, tf in enumerate(self.GN_target_frequencies):
            gain, noise_T = self.gain_noise(self.GN_frequencies, np.asarray(self.GN_P)[:, tf_id,:], temp_files[0][0], temp_files[1][0], bw)
            self.G[tf_id, :] = gain
            self.TN[tf_id, :] = noise_T
            self.G_1d[tf_id] = np.interp(tf, self.GN_frequencies, gain)
            self.TN_1d[tf_id] = np.interp(tf, self.GN_frequencies, noise_T)
            #print (noise_powers)
            
        self.GN_meas = {'Gain frequency dependence': (('Target frequency', 'Probe frequency'), 
                         (self.GN_target_frequencies, self.GN_frequencies),
                         self.G, {'log':10}),
                        'Noise T frequency dependence': (('Target frequency', 'Probe frequency'), 
                         (self.GN_target_frequencies, self.GN_frequencies),
                         self.TN),
                        'Gain': (('Frequency',), (self.GN_target_frequencies,), self.G_1d, {'log':10}),
                        'Noise T': (('Frequency',), (self.GN_target_frequencies,), self.TN_1d),}
        self.off_gain = np.nanmedian(np.nanmedian(self.G))
        return self.GN_meas
        
    def load_vna_noise_measurement(self, filename, vna_power, bw, atten):
        from scipy.constants import Boltzmann
        noise_vna = open('D:\\qtlab\\ReiData\\data\\2017-06-23\\10-52-50\\S-parameter S-paramter with std -60 dBm, bw 5e4.pkl', 'rb')
        data_vna = pickle.load(noise_vna)
        noise_vna.close()
        noise_rel = (np.real(data_vna[1]['S-parameter std'][2])/np.abs(data_vna[1]['S-parameter'][2]))**2
        noise_vna_inp = 1e-3*(10**(vna_power/10.))
        noise_T = noise_rel*noise_vna_inp*(10**(atten/10))/(bw*Boltzmann)
        gain = (np.abs(data_vna[1]['S-parameter'][2])**2)*10**(-atten/10)
        self.TN_m = noise_T
        self.G_m = gain
        self.GN_m_target_frequencies = data_vna[1]['S-parameter'][1][0]
        self.GN_m_probe_frequencies = data_vna[1]['S-parameter'][1][1]
        self.G_m_1d = np.zeros(self.GN_m_target_frequencies.shape[0])
        self.TN_m_1d = np.zeros(self.GN_m_target_frequencies.shape[0])
        for tf_id, tf in enumerate(self.GN_m_target_frequencies):
            self.G_m_1d[tf_id] = np.interp(tf, self.GN_m_probe_frequencies, gain[tf_id,:])
            self.TN_m_1d[tf_id] = np.interp(tf, self.GN_m_probe_frequencies, noise_T[tf_id,:])
        
        self.off_gain_m = np.nanmedian(self.G_m)
        
        self.GN_m_meas = {'Monochromatic gain frequency dependence': (('Target frequency', 'Probe frequency'), 
                         (self.GN_m_target_frequencies, self.GN_m_probe_frequencies),
                         self.G_m, {'log':10}),
                        'Monochromatic noise T frequency dependence': (('Target frequency', 'Probe frequency'), 
                         (self.GN_m_target_frequencies, self.GN_m_probe_frequencies),
                         self.TN_m),
                        'Monochromatic gain': (('Frequency',), (self.GN_m_target_frequencies,), self.G_m_1d, {'log':10}),
                        'Monochromatic noise T': (('Frequency',), (self.GN_m_target_frequencies,), self.TN_m_1d),}
        self.off_gain = np.nanmedian(np.nanmedian(self.G))
        return self.GN_meas
            
    def load_gain_saturation_measurement(self, filename, filter_kernel = (3,3,3)):
        import pickle
        from scipy.signal import medfilt, convolve
        file = open(filename, 'rb')
        data = pickle.load(file)
        data_power = np.abs(data[1]['S-parameter'][2])**2
        filter_kernel = np.ones(filter_kernel)
        data_power_filt = np.transpose(convolve(data_power, filter_kernel/np.sum(filter_kernel), mode='same'), axes=(1,0,2))
        file.close()
        data_filt_diff = np.log10(data_power_filt/data_power_filt[0,:,:])*10
        data_filt_uncompressed = (data_filt_diff>-1)
        pp, tf, pf = np.meshgrid(data[1]['S-parameter'][1][1], 
                                 data[1]['S-parameter'][1][0], 
                                 data[1]['S-parameter'][1][2], 
                                 indexing='ij')
        pp[data_filt_uncompressed]=np.nan
        pp_compression = np.nanmin(pp, axis=0)
        
        compression_1db_1d = np.zeros(data[1]['S-parameter'][1][0].shape, dtype=float)
        for tf_id, _tf in enumerate(data[1]['S-parameter'][1][0]):
            compression_1db_1d[tf_id] = np.interp(_tf, data[1]['S-parameter'][1][2], pp_compression[tf_id,:])
        
        self.sat_1db_ft_freq = pp_compression
        self.sat_1db_ft = compression_1db_1d
        
        self.sat_target_freq = data[1]['S-parameter'][1][0]
        self.sat_freq = data[1]['S-parameter'][1][2]
        
        self.sat_meas = data[1]
        self.sat_meas['1 dB compression point on frequency'] = (('Target frequency', 'Probe frequency'), \
                                                       (self.sat_target_freq, self.sat_freq), self.sat_1db_ft_freq)
        self.sat_meas['1 dB compression point'] = (('Frequency',), (self.sat_target_freq,), self.sat_1db_ft)
        
        return self.sat_meas
    
    def save_gain_saturation_plots(self, name):
        import save_pkl
        calibration_path = get_config().get('datadir')+'/calibrations/paramp/saturation/{0}/'.format(name)
        header = {'name':name, 'type':'gain saturation'}
        save_pkl.save_pkl(header, self.sat_meas, location=calibration_path)
        
    def save_gain_noise_plots(self, name):
        import save_pkl
        calibration_path = get_config().get('datadir')+'/calibrations/paramp/gain & noise/{0}/'.format(name)
        header = {'name':name, 'type':'gain & noise'}
        save_pkl.save_pkl(header, self.GN_meas, location=calibration_path)

    def save_vna_gain_noise_plots(self, name):
        import save_pkl
        calibration_path = get_config().get('datadir')+'/calibrations/paramp/monochromatic gain & noise/{0}/'.format(name)
        header = {'name':name, 'type':'Monochromatic gain & noise'}
        save_pkl.save_pkl(header, self.GN_m_meas, location=calibration_path)
            
    def planck_function(self, f, Ts, gains):
        from scipy.constants import Planck, Boltzmann
        return np.sum([Planck*f*(0.5+1./(np.exp(Planck*f/(Boltzmann*T))-1))*gain for T, gain in zip(Ts, gains)])

    def gain_noise(self, f, P_meas, T1, T2, bw):
        from scipy.constants import Boltzmann
        G_ = np.zeros_like(f)
        TN_ = np.zeros_like(f)
        P_meas = np.asarray(P_meas)*1e-3
        for f_id, f_ in enumerate(f):
            P_in = [self.planck_function(f_, 
                                         [t[0] for t in T1], 
                                         [t[1] for t in T1]), 
                    self.planck_function(f_, 
                                         [t[0] for t in T2], 
                                         [t[1] for t in T2])] # input noise powers
            a = np.asarray([[1, P_in[0]*bw], [1, P_in[1]*bw]])
            b = P_meas[:, f_id].T
            #print (f_id, a.shape, b.shape)
            solution = np.linalg.solve(a, b)
            #print (solution)
            #if (f_id<10):
                #print (a,b, solution)
            GkTNbw, G = solution
            TN = GkTNbw/(Boltzmann*G*bw)
            G_[f_id] = G
            TN_[f_id] = TN
        return G_, TN_
    
    def set_target_freq_calib(self, f):
        self.pump_src.set_frequency(self.pump_frequency_by_target_frequency(f))
        self.pump_src.set_power(self.pump_power_by_target_frequency(f))
        self.bias_src.set_current(self.bias_by_target_frequency(f))
        
    def calibrate_vna(self, frequencies, name):
        calibration_path = get_config().get('datadir')+'/calibrations/paramp/calibration'
        calibration = sweep.sweep(self, 
                                  (frequencies, paramp.set_target_f, 'Target frequency'), 
                                  filename='Paramp VNA calibration {0}'.format(name), 
                                  output=False, 
                                  location=calibration_path)
        self.load_calibration(calibration_path, name)

In [16]:
import qsweepy.paramp as paramp
imp.reload(paramp)
from qsweepy.paramp import paramp

In [44]:
#paramp = paramp(pna, lo1, current_src)
paramp = paramp(None, None, None)
paramp.set_target_f(5e9)
paramp.set_target_bw(600e3)
paramp.set_target_power(-50)
paramp.hint_maxfun = 50
paramp.pump_on = True

meas_noise = paramp.load_noise_measurement(((((3.41, 0.1), (0.040, 0.9)), 'D:\\qtlab\\ReiData\\data\\2017-06-21\\20-52-53\\Power Noise 341mK.pkl'),
                               (((0.040, 1.0),), 'D:\\qtlab\\ReiData\\data\\2017-06-21\\23-24-58\\Power Noise 40mK.pkl')), bw=3e5)
meas_saturation = paramp.load_gain_saturation_measurement('D:\\qtlab\\ReiData\\data\\2017-06-22\\10-12-10\\S-parameter VNA Gain Saturation.pkl')

file = open('D:\\qtlab\\ReiData\\data\\2017-06-22\\17-21-47\\Power VNA -70 dBm power on SA, bw 5e4.pkl', 'rb')
data = pickle.load(file)
file.close()
paramp.attenuation = np.nanmedian(data[1]['Power'][2])-np.log10(np.nanmedian(paramp.G))*10+70
print (paramp.attenuation)

meas_noise_m = paramp.load_vna_noise_measurement(\
                filename='D:\\qtlab\\ReiData\\data\\2017-06-23\\10-52-50\\S-parameter S-paramter with std -60 dBm, bw 5e4.pkl', \
                bw=5e4, atten=paramp.attenuation, vna_power=-60)

KeyboardInterrupt: 

In [12]:
sa.measure()['Power'], sa.get_points()['Power'][0][1]

IndexError: list index out of range

In [14]:
plt.plot(sa.get_points()['Power'][0][1], sa.measure()['Power'])

In [11]:
paramp0 = paramp(pna, lo1, current_src)
#paramp = paramp(None, None, None)
paramp0.set_target_f(7e9)
paramp0.set_target_bw(600e3)
paramp0.set_target_power(-50)
paramp0.hint_maxfun = 50
paramp0.pump_on = True


In [168]:
paramp.save_gain_saturation_plots('Kulesh 3SQ 4wave')
paramp.save_gain_noise_plots('Kulesh 3SQ 4wave')
paramp.save_vna_gain_noise_plots('Kulesh 3SQ 4wave')

c:\python36\lib\site-packages\matplotlib\backend_bases.py:2445: MatplotlibDeprecationWarning: Using default event loop until function specific to this GUI is implemented
  warnings.warn(str, mplDeprecation)
D:\qtlab_replacement\scripts\plotting.py:41: RuntimeWarning: divide by zero encountered in log10
  elif log == 10:									filter_abs = lambda x: np.log10(np.abs(x))*10


In [47]:
plt.figure()
plt.pcolormesh(np.log10(paramp.G)*10, vmin=40, vmax=80)
plt.colorbar()
plt.figure()
plt.pcolormesh(paramp.TN, vmin=0, vmax=10)
plt.colorbar()

c:\python36\lib\site-packages\ipykernel_launcher.py:2: RuntimeWarning: divide by zero encountered in log10
  
c:\python36\lib\site-packages\ipykernel_launcher.py:2: RuntimeWarning: invalid value encountered in log10
  


c:\python36\lib\site-packages\matplotlib\colors.py:494: RuntimeWarning: invalid value encountered in less
  cbook._putmask(xa, xa < 0.0, -1)


510046.62923161994

In [54]:
np.log10(np.nanmean(paramp.G[np.isfinite(paramp.TN)]))*10

43.717889941409204

In [102]:
paramp.Gn = paramp.G.copy()
paramp.Gn[paramp.Gn<0]=0
paramp.TNn = paramp.TN.copy()
paramp.TNn[paramp.TNn<0]=0
paramp.TNn[np.isinf(paramp.TNn)]=0

In [112]:
plt.figure()
plt.pcolormesh(np.abs(data_filt_diff[:,0,:]))
plt.colorbar()

c:\python36\lib\site-packages\matplotlib\colors.py:494: RuntimeWarning: invalid value encountered in less
  cbook._putmask(xa, xa < 0.0, -1)


In [48]:
freqs = np.linspace(5.0e9, 7.0e9, 201)
lo1.set_power(7.12)
lo1.set_frequency(5e9)
current_src.set_current(100e-6)

True

In [12]:
paramp0.set_target_f(7.0e9)
paramp0.measure()

root: WARNING  Setting a boolean, but that is not the expected type


[14080000000.0, 8.74, 3.963e-05]
-18.5853289308 -2.91401058777
[  1.40814080e+10   8.74000000e+00   3.96300000e-05] 0.511209529826
-17.984282063 -3.65535703074
[  1.40800000e+10   8.82740000e+00   3.96300000e-05] 0.43098712537
-18.2432347045 -3.48116974045
[  1.40800000e+10   8.74000000e+00   4.00263000e-05] 0.448624539917
-18.4340435421 -3.18294864386
[  1.40800000e+10   8.74000000e+00   3.96300000e-05] 0.480512993213
-18.6343805291 -2.82721252833
[  1.40785920e+10   8.79826667e+00   3.98942000e-05] 0.521529341612
-18.8537002432 -2.75054433904
[  1.40807040e+10   8.75456667e+00   3.96960500e-05] 0.530817908038
-18.5476082782 -2.92928494897
[  1.40800000e+10   8.78370000e+00   3.98281500e-05] 0.50941473755
-18.4175361435 -3.04261159447
[  1.40800000e+10   8.78370000e+00   3.96300000e-05] 0.496293789474
-18.1664331297 -3.46219472336
[  1.40807040e+10   8.78370000e+00   3.96300000e-05] 0.450588940194
-18.4710617227 -2.90908444222
[  1.40804693e+10   8.81283333e+00   3.94318500e-05] 0.511

{'Bias': array(3.9617615625000004e-05),
 'Pump frequency': array(14080073333.333332),
 'Pump power': array(8.821027083333334),
 'S-parameter': array((-0.12135059386491776-0.04249921068549156j)),
 'SNR': array(0.5399698190683837)}

In [49]:
sweep.sweep(paramp0, (freqs, paramp0.set_target_f, 'Target frequency'), filename='Paramp VNA calib', output=False)

A Jupyter Widget

Started at:  May 03 2018 17:56:59


C:\ProgramData\Anaconda3\lib\site-packages\matplotlib\cbook\deprecation.py:106: MatplotlibDeprecationWarning: Adding an axes using the same arguments as a previous axes currently reuses the earlier instance.  In a future version, a new instance will always be created and returned.  Meanwhile, this warning can be suppressed, and the future behavior ensured, by passing a unique label to each axes instance.
  warnings.warn(message, mplDeprecation, stacklevel=1)
root: WARNING  Setting a boolean, but that is not the expected type


[5000000000.0, 7.12, 0.0001]
-10.9657858081 4.75539254718
[  5.00050000e+09   7.12000000e+00   1.00000000e-04] 2.98909181077
-7.44423570925 7.5033432973
[  5.00000000e+09   7.19120000e+00   1.00000000e-04] 5.62774394953
-7.41591165855 7.44311894308
[  5.00000000e+09   7.12000000e+00   1.01000000e-04] 5.55024167786
-10.7212353996 9.13232432711
[  5.00000000e+09   7.12000000e+00   1.00000000e-04] 8.18902944533
-11.0580537179 7.44650373262
[  5.00033333e+09   7.16746667e+00   1.00666667e-04] 5.55456909244
-11.0769825856 3.52660705778
[  5.00055556e+09   7.08044444e+00   1.01111111e-04] 2.25247876693
-11.1536723537 -6.99685188254
[  5.00083333e+09   7.02506667e+00   1.01666667e-04] 0.199670916671
-11.044831952 3.49019090568
[  5.00055556e+09   7.00924444e+00   1.01111111e-04] 2.23367040759
-11.0102087329 -7.04109036229
[  5.00125926e+09   6.98287407e+00   1.00851852e-04] 0.197647335414
-11.0307594532 -7.04530848315
[  5.00188889e+09   6.91431111e+00   1.00777778e-04] 0.197455462009
-11.235

root: WARNING  Setting a boolean, but that is not the expected type


...

root: WARNING  Setting a boolean, but that is not the expected type


[5188294690.279, 11.86, 7.32e-06]
-14.5260246466 -5.30967265773
[  5.18881352e+09   1.18600000e+01   7.32000000e-06] 0.294464357306
-13.9355874881 -5.56848300842
[  5.18829469e+09   1.19786000e+01   7.32000000e-06] 0.277428899518
-14.633527893 -5.25847120838
[  5.18829469e+09   1.18600000e+01   7.39320000e-06] 0.297956510324
-14.6813369966 -5.28853240803
[  5.18829469e+09   1.18600000e+01   7.32000000e-06] 0.295901222342
-14.0551987564 -5.55476140852
[  5.18864058e+09   1.19390667e+01   7.24680000e-06] 0.278306826507
-13.7732067032 -5.60021595967
[  5.18887117e+09   1.19917778e+01   7.27120000e-06] 0.275409174845
-13.3246698973 -5.76360261222
[  5.18915941e+09   1.20576667e+01   7.24680000e-06] 0.265240439449
-13.2178555997 -5.63142756706
[  5.18858293e+09   1.21235556e+01   7.22240000e-06] 0.273436976535
-13.0567258582 -5.58032112565
[  5.18871744e+09   1.21674815e+01   7.27933333e-06] 0.276673706002
-12.9631625829 -5.5062705772
[  5.18934516e+09   1.22538691e+01   7.17902222e-06] 0.2

root: WARNING  Setting a boolean, but that is not the expected type


[5199579217.963, 11.96, 6.94e-06]
-12.1411704049 -6.44350309724
[  5.20009918e+09   1.19600000e+01   6.94000000e-06] 0.226803467638
-11.629950586 -6.43776630079
[  5.19957922e+09   1.20796000e+01   6.94000000e-06] 0.227103260778
-12.3098777608 -6.4149320006
[  5.19957922e+09   1.19600000e+01   7.00940000e-06] 0.228300467041
-12.3666002928 -6.31793223247
[  5.19957922e+09   1.19600000e+01   6.94000000e-06] 0.233456933536
-11.7192438309 -6.56237615556
[  5.19992586e+09   1.20397333e+01   6.98626667e-06] 0.220679699773
-11.513108235 -6.57248431191
[  5.20009918e+09   1.20796000e+01   7.00940000e-06] 0.220166667467
-11.3822732312 -6.43892907584
[  5.20027250e+09   1.21194667e+01   6.91686667e-06] 0.227042464551
-11.5300933842 -6.63579534413
[  5.20073468e+09   1.20264444e+01   6.97084444e-06] 0.21698038007
-11.488816159 -6.67350444222
[  5.20131241e+09   1.19998667e+01   6.98626667e-06] 0.215104529632
-12.2733049029 -6.36816784959
[  5.20073468e+09   1.19068444e+01   7.04024444e-06] 0.2307

{'Bias': (('Target frequency',),
  (array([  5.00000000e+09,   5.01000000e+09,   5.02000000e+09,
            5.03000000e+09,   5.04000000e+09,   5.05000000e+09,
            5.06000000e+09,   5.07000000e+09,   5.08000000e+09,
            5.09000000e+09,   5.10000000e+09,   5.11000000e+09,
            5.12000000e+09,   5.13000000e+09,   5.14000000e+09,
            5.15000000e+09,   5.16000000e+09,   5.17000000e+09,
            5.18000000e+09,   5.19000000e+09,   5.20000000e+09,
            5.21000000e+09,   5.22000000e+09,   5.23000000e+09,
            5.24000000e+09,   5.25000000e+09,   5.26000000e+09,
            5.27000000e+09,   5.28000000e+09,   5.29000000e+09,
            5.30000000e+09,   5.31000000e+09,   5.32000000e+09,
            5.33000000e+09,   5.34000000e+09,   5.35000000e+09,
            5.36000000e+09,   5.37000000e+09,   5.38000000e+09,
            5.39000000e+09,   5.40000000e+09,   5.41000000e+09,
            5.42000000e+09,   5.43000000e+09,   5.44000000e+09,
       

In [52]:
lo1.set_status(0)
lo1.set_frequency(9.5e9)
lo1.set_power(18)
pna.set_nop(1001)
measurement = pna.measure()
plt.figure('Gain')

pna.set_xlim(3e9, 5e9)
plt.plot(pna.get_points()['S-parameter'][0][1], np.log10(np.abs(measurement['S-parameter']))*20)

In [19]:
pna.get_points()['S-parameter']

{'S-parameter': [('Frequency',
   array([  4.00000000e+09,   4.00004001e+09,   4.00008002e+09, ...,
            4.19991998e+09,   4.19995999e+09,   4.20000000e+09]),
   'Hz')]}

## load optimized calibration of drive power&freq and bias

In [59]:
import pickle
savepath='D:\\qtlab\\ReiData\\data\\2017-11-16\\22-41-06\\'
name=''
#paramp = paramp(pna, lo1, current_src)
paramp0.load_calibration(savepath, name )

In [23]:
paramp.set_target_freq_calib(7.80e9)

In [26]:
sa.set_xlim(7.5e9, 8.3e9)
sa.set_nop(3001)
sa.set_res_bw(3e5)
sa.set_video_bw(1e3)
sweep.sweep(sa, (freqs, paramp.set_target_freq_calib, 'Target frequency'), filename='Noise 40mK')

Started at:  Jun 21 2017 23:24:58
First sweep...

c:\python36\lib\site-packages\matplotlib\backend_bases.py:2445: MatplotlibDeprecationWarning: Using default event loop until function specific to this GUI is implemented
  warnings.warn(str, mplDeprecation)


Time left: 0 h 0 m 0.0 s,	parameter values: Target frequency: 7.9e+09,	average cycle time:  5.8s	8s			
Elapsed time: 0 h 11 m 45.28 s


TypeError: Could not convert None (type <class 'NoneType'>) to array

In [112]:
pna.set_xlim(7.5e9, 8.3e9)
pna.set_nop(1001)
pna.set_bandwidth(1e3)
probe_powers = np.linspace(-75, -45, 31)
sweep.sweep(pna, (freqs, paramp.set_target_freq_calib, 'Target frequency'), 
            (probe_powers, pna.set_power, 'Probe power'), 
            filename='VNA Gain Saturation')

Started at:  Jun 22 2017 10:12:10
First sweep...

c:\python36\lib\site-packages\matplotlib\backend_bases.py:2445: MatplotlibDeprecationWarning: Using default event loop until function specific to this GUI is implemented
  warnings.warn(str, mplDeprecation)


Time left: 0 h 0 m 0.0 s,	parameter values: Target frequency: 7.9e+09,	Probe power:    -45,	average cycle time:  3.6s			s		
Elapsed time: 3 h 45 m 25.69 s


{'S-parameter': (('Target frequency', 'Probe power', 'Frequency'),
  (array([  7.56000000e+09,   7.56283333e+09,   7.56566667e+09,
            7.56850000e+09,   7.57133333e+09,   7.57416667e+09,
            7.57700000e+09,   7.57983333e+09,   7.58266667e+09,
            7.58550000e+09,   7.58833333e+09,   7.59116667e+09,
            7.59400000e+09,   7.59683333e+09,   7.59966667e+09,
            7.60250000e+09,   7.60533333e+09,   7.60816667e+09,
            7.61100000e+09,   7.61383333e+09,   7.61666667e+09,
            7.61950000e+09,   7.62233333e+09,   7.62516667e+09,
            7.62800000e+09,   7.63083333e+09,   7.63366667e+09,
            7.63650000e+09,   7.63933333e+09,   7.64216667e+09,
            7.64500000e+09,   7.64783333e+09,   7.65066667e+09,
            7.65350000e+09,   7.65633333e+09,   7.65916667e+09,
            7.66200000e+09,   7.66483333e+09,   7.66766667e+09,
            7.67050000e+09,   7.67333333e+09,   7.67616667e+09,
            7.67900000e+09,   7.68183

In [ ]:
sa.set_span(0)
sa.set_nop(1)
sa.set_res_bw(5e4)
sa.set_video_bw(1e2)
pna.set_power(-70)
pna.set_nop(1)
probe_freqs = np.linspace(7.5e9, 8.3e9, 401)
sweep.sweep(sa, (freqs, paramp.set_target_freq_calib, 'Target frequency'), 
            (probe_freqs, lambda x: (pna.set_xlim(x, x), sa.set_xlim(x,x)), 'Probe frequency'), 
            filename='VNA -70 dBm power on SA, bw 5e4', output=False)

Started at:  Jun 22 2017 17:21:47


c:\python36\lib\site-packages\matplotlib\backend_bases.py:2445: MatplotlibDeprecationWarning: Using default event loop until function specific to this GUI is implemented
  warnings.warn(str, mplDeprecation)


Time left: 4 h 19 m 39.72 s,	parameter values: Target frequency: 7.668e+09,	Probe frequency: 7.68e+09,	average cycle time: 0.47s		

In [67]:
import data_reduce
pna.set_power(-65)
pna.set_nop(10001)
pna.set_span(0)
pna.set_bandwidth(100e3)

vna_std = data_reduce.data_reduce(pna)
vna_std.filters = {'S-parameter': data_reduce.mean_reducer(pna, 'S-parameter', 0),
                   'S-parameter std': data_reduce.std_reducer(pna, 'S-parameter', 0)}

freqs = np.linspace(3.5335e9, 4.5335e9, 1001)
sweep.sweep(vna_std, (freqs, pna.set_centerfreq, 'Probe frequency'), 
            filename='S-parameter with std -65 dBm, bw 100kHz 1e5 points paramp on')
lo1.set_status(0)
sweep.sweep(vna_std, (freqs, pna.set_centerfreq, 'Probe frequency'), 
            filename='S-parameter with std -65 dBm, bw 100kHz 1e5 points paramp off')

A Jupyter Widget

Started at:  May 04 2018 21:15:26

Elapsed time: 0 h 9 m 18.72 s


C:\ProgramData\Anaconda3\lib\site-packages\matplotlib\cbook\deprecation.py:106: MatplotlibDeprecationWarning: Adding an axes using the same arguments as a previous axes currently reuses the earlier instance.  In a future version, a new instance will always be created and returned.  Meanwhile, this warning can be suppressed, and the future behavior ensured, by passing a unique label to each axes instance.
  warnings.warn(message, mplDeprecation, stacklevel=1)


A Jupyter Widget

Started at:  May 04 2018 21:24:47


C:\ProgramData\Anaconda3\lib\site-packages\matplotlib\cbook\deprecation.py:106: MatplotlibDeprecationWarning: Adding an axes using the same arguments as a previous axes currently reuses the earlier instance.  In a future version, a new instance will always be created and returned.  Meanwhile, this warning can be suppressed, and the future behavior ensured, by passing a unique label to each axes instance.
  warnings.warn(message, mplDeprecation, stacklevel=1)



Elapsed time: 0 h 12 m 28.77 s


{'S-parameter': (('Probe frequency',),
  (array([  3.53350000e+09,   3.53450000e+09,   3.53550000e+09, ...,
            4.53150000e+09,   4.53250000e+09,   4.53350000e+09]),),
  array([-0.00037373-0.00078521j,  0.00036538+0.0007969j ,
          0.00062919+0.00061771j, ..., -0.00174369+0.00144863j,
          0.00180062-0.00140695j, -0.00118116+0.00193847j]),
  {'log': 20},
  ('',)),
 'S-parameter std': (('Probe frequency',),
  (array([  3.53350000e+09,   3.53450000e+09,   3.53550000e+09, ...,
            4.53150000e+09,   4.53250000e+09,   4.53350000e+09]),),
  array([ 0.00072434+0.j,  0.00071774+0.j,  0.00072191+0.j, ...,
          0.00082864+0.j,  0.00081914+0.j,  0.00081927+0.j]),
  {'log': 20},
  ('',))}

In [ ]:
std_reduce = 

In [11]:
# four-frequency lower sideband
lo1.set_frequency(7.786e9)
lo1.set_power(13.45)
current_src.set_current(86.60e-6)
# lower f: 7.560e9, upper: 7.922e9

True

In [38]:
#three-frequency
current_src.set_current(80.43e-6)
lo1.set_frequency(16.351e9)
lo1.set_power(0.48)

True

In [10]:
current_src.set_current(84.01e-6)
lo1.set_frequency(7.92e9)
lo1.set_power(4.7)

True

In [39]:
# four-wave mixing, upper sideband
current_src.set_current(82.01e-6)
lo1.set_frequency(7.9942e9)
lo1.set_power(-0.44)
#8.081GHz

True

In [29]:
lo1.set_status(True)
pna.set_xlim(7.8e9, 8.2e9)
pna.set_nop(1001)
pna.set_bandwidth(1e5)
plt.plot(pna.get_freqpoints(), np.log10(pna.get_tracedata()[0])*20)

c:\python36\lib\site-packages\matplotlib\backend_bases.py:2445: MatplotlibDeprecationWarning: Using default event loop until function specific to this GUI is implemented
  warnings.warn(str, mplDeprecation)


In [30]:
current_src.set_current(-62.74e-6)
lo1.set_frequency(8.6432e9)
lo1.set_power(-5)
target_freqs = np.arange(8.081e9, 7.800e9, 1e6)
optim_params = [paramp_optimize(pna, f, 1e3, -45, lo1, current_src, fp_guess=f+0.2e6, initial_simplex=simplex, maxfun=40) for f in target_freqs]

NameError: name 'paramp_optimize' is not defined

In [10]:
m = sweep.sweep(sa, (pump_powers, lo1.set_power, 'Excitation power'), \
                        filename='WTJPA Ic6.9uA res pump{0:2.4f}GHz switch 1'.format(pump_freq/1e9))

NameError: name 'pump_powers' is not defined

In [10]:
rf_switch.do_set_switch(2, channel=sw_ch)

In [19]:
plt.figure()
plt.pcolormesh(T1_noise['Power'][1][1], T1_noise['Power'][1][0], T1_noise['Power'][2]);
plt.colorbar()

In [20]:
plt.figure()
plt.pcolormesh(T2_noise['Power'][1][1], T2_noise['Power'][1][0],T2_noise['Power'][2]);
plt.colorbar()

In [21]:
plt.figure()
plt.pcolormesh(T2_noise['Power'][1][1], T2_noise['Power'][1][0], T1_noise['Power'][2]-T2_noise['Power'][2]);
plt.colorbar()

In [8]:
points = sa.get_points()
dtypes = sa.get_dtype()
meas = sa.measure()

In [9]:
pna_points = pna.get_points()
pna_dtypes = pna.get_dtype()
pna_meas = pna.measure()

In [10]:
print(points['Power'][0][1].shape)
print(pna_points['S-parameter'][0][1].shape)
print(dtypes)
print(pna_dtypes)
print(meas['Power'].shape)
print(pna_meas['S-parameter'].shape)

(1000,)
(201,)
{'Power': <class 'float'>}
{'S-parameter': <class 'complex'>}
(1000,)
(201,)


### Загрузка данных

In [36]:
filename = 'Noise & Gain JPA Ic6.9uA res'
location = 'D:\\qtlab\\ReiData\\data\\2017-06-15\\13-33-17'
data = load_pkl(filename, location=location)[1]

D:\qtlab\ReiData\data\2017-06-15\13-33-17/Noise & Gain JPA Ic6.9uA res.pkl


In [37]:
gains = data['Gain']
noise_Ts= data['Noise Temp']

In [199]:
data_cropped = data.copy()
data_cropped['S-parameter'] = (data_cropped['S-parameter'][0], \
                               (data_cropped['S-parameter'][1][0], data_cropped['S-parameter'][1][1][150:]), \
                               data_cropped['S-parameter'][2][:,150:])
data_cropped_amp = data.copy()
data_cropped_amp['S-parameter'] = (data_cropped['S-parameter'][0], \
                               (data_cropped['S-parameter'][1][0], data_cropped['S-parameter'][1][1]), \
                               convolve2d(data_cropped['S-parameter'][2], np.ones((4,4)), mode='same'))

In [190]:
convolve2d(data_cropped['S-parameter'][2], np.ones((1,1)), mode='same')[:,150:].shape

(401, 201)

In [234]:
import fitting
import imp
imp.reload(fitting)
from scipy.signal import convolve2d

In [235]:
results = fitting.dc_squid_fit_S21(data_cropped_amp, noise_sigma=3, fit=False, method='diff_curr', plot=True)

c:\python36\lib\site-packages\numpy\core\fromnumeric.py:2889: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
c:\python36\lib\site-packages\numpy\core\_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


In [228]:
results.keys()

dict_keys(['fitresults', 'evaluator', 'fp_est', 'fp_est_xpoints'])

In [237]:
results['fitresults']

{'I0': 5.1017243648743762e-05,
 'L': 4234.4902819693152,
 'a': 1.0000386770339402,
 'b': -1.0000298591138239,
 'fp': 3425223051.333847}

In [238]:
plt.figure()
plt.pcolormesh(*data_cropped['S-parameter'][1], np.abs(data_cropped['S-parameter'][2]).T)
plt.scatter(results['fp_est_xpoints'],results['fp_est'])
plt.plot(data_cropped['S-parameter'][1][0], results['evaluator'](data_cropped['S-parameter'][1][0]))
plt.xlim([np.min(data_cropped['S-parameter'][1][0]), np.max(data_cropped['S-parameter'][1][0])])
plt.ylim([np.min(data_cropped['S-parameter'][1][1]), np.max(data_cropped['S-parameter'][1][1])])

(2100000000.0, 3500000000.0)

In [15]:
S21 = data['S-parameter'][2]
currents = data['S-parameter'][1][0]
frequencies = data['S-parameter'][1][1]
fitresults = [None]*currents.size

In [5]:
from scipy.ndimage.filters import gaussian_filter
from scipy.optimize import leastsq
bgremove = np.sum(S21[0:2,:], axis=0)/3
_S21 = S21
S21 = S21/bgremove
#_S21_filt = (gaussian_filter(np.real(_S21), 2)+1j*gaussian_filter(np.imag(_S21), 2))
delay = -(np.unwrap(np.angle(bgremove))[-1] - np.unwrap(np.angle(bgremove))[0])/(2*np.pi*(frequencies[-1]-frequencies[0]))
plt.figure('S21')
diff = np.gradient((gaussian_filter(np.real(S21), 3)+1j*gaussian_filter(np.imag(S21), 3)))[1]/(frequencies[1]-frequencies[0])
diff2 = np.gradient((np.real(diff)+1j*np.imag(diff)))[1]/(frequencies[1]-frequencies[0])
plt.pcolormesh(currents, frequencies, np.abs(S21.T))#np.abs(np.gradient(S21.T)[1]))
res_freq_id_estimate = np.argmin(np.abs(S21), axis=1)
res_freq_estimate = frequencies[res_freq_id_estimate]
#delay_mesh = -np.gradient(np.unwrap(np.angle(_S21_filt)))[1]/((frequencies[1]-frequencies[0])*2*np.pi)-delay
#delay2_mesh = np.gradient(delay_mesh)[1]/((frequencies[1]-frequencies[0])*2*np.pi)
res_delay = diff[[i for i in range(currents.size)], res_freq_id_estimate]
res_delay_deriv = diff2[[i for i in range(currents.size)], res_freq_id_estimate]
lifetime = res_delay_deriv/res_delay*1j/(np.pi)
Q = (lifetime*res_freq_estimate)/2.
C = lifetime/(2*50) # in Farads
L = 1/((2*np.pi*res_freq_estimate)**2*C)
#res_freq_estimate_unreliable = np.zeros(currents.shape, dtype=bool)
res_freq_estimate_unreliable = np.min(np.abs(S21), axis=1)>np.mean(np.abs(S21))-3*np.std(np.abs(S21))
for cur_id, cur in enumerate(currents):
    if cur_id < 1 or cur_id >= currents.size-1:
        continue
    if (np.abs(res_freq_estimate[cur_id]-np.mean(res_freq_estimate[cur_id-3:cur_id+3])))>(np.max(frequencies)-np.min(frequencies))*0.1:
        res_freq_estimate_unreliable[cur_id] = True

res_freq_estimate[res_freq_estimate_unreliable] = np.nan
fit_unreliable = np.zeros(currents.shape, dtype=bool)
plt.plot(currents, res_freq_estimate)
fit_fr = np.zeros(currents.shape)
fit_Qc = np.zeros(currents.shape)
fit_Ql = np.zeros(currents.shape)
fit_Qi = np.zeros(currents.shape)
Qc_column_name = 'Qc'
Qi_column_name = 'Qi'
Ql_column_name = 'Ql'

fit = False
if fit:
    last_freq = False
    span = 80e6
    for cur_id, cur in enumerate(currents):
        fit_unreliable[cur_id] = True
        if not last_freq and np.isfinite(res_freq_estimate[cur_id]):
            f0 = res_freq_estimate[cur_id]
        elif np.isfinite(last_freq):
            f0 = last_freq
        else:
            continue
        
        if (f0-span/2.<np.min(frequencies) or f0+span/2.>np.max(frequencies)):
            last_freq = False
            continue
        
        freq_mask = (frequencies>f0-span/2.)*(frequencies<f0+span/2.)
        f_data = frequencies[freq_mask]
        z_data = S21[cur_id, :][freq_mask]
        
        fitter = circuit.reflection_port(f_data=f_data, z_data_raw=z_data)
        fitter.autofit()
        fitresults[cur_id] = fitter.fitresults
        fit_fr[cur_id] = fitresults[cur_id]['fr']
        fit_Qc[cur_id] = fitresults[cur_id][Qc_column_name]
        fit_Qi[cur_id] = fitresults[cur_id][Qi_column_name]
        fit_Ql[cur_id] = fitresults[cur_id][Ql_column_name]
        fit_unreliable[cur_id] = (1-(fit_fr[cur_id]<np.nanmax(f_data))*(fit_fr[cur_id]>np.nanmin(f_data)))>0
        
    fit_fr[fit_unreliable] = np.nan
    fit_Qi[fit_unreliable] = np.nan
    fit_Qc[fit_unreliable] = np.nan
    fit_Ql[fit_unreliable] = np.nan
    #plt.plot(currents, fit_fr)
    #plt.ylim([np.min(frequencies), np.max(frequencies)])
    #plt.figure('Qc')
    fit_Qc[fit_Qc>1e5]=np.nan
    fit_Qc[fit_Qc<0]=np.nan
    
# fitting res_freq_estimate to theoretical
ft = lambda I,fp,I0,L,a,b: np.real(fp*(1+b)*(1/(1/np.sqrt((1-a)*np.abs(np.cos((I-I0)*L).astype(np.complex))+a)+b)))
ft_x = lambda I,x: ft(I, x[0], x[1], x[2], x[3], x[4])
currents_freq_estimate = currents[np.isfinite(res_freq_estimate)]
cost = lambda x: ft_x(currents_freq_estimate, x)-res_freq_estimate[np.isfinite(res_freq_estimate)]
max_freq_cur_id = np.nanargmax(res_freq_estimate)
max_freq = np.nanmax(res_freq_estimate)
cur_h = 3
d2fdI2 = (res_freq_estimate[max_freq_cur_id+cur_h]+res_freq_estimate[max_freq_cur_id-cur_h]-2*res_freq_estimate[max_freq_cur_id])/\
            ((currents[max_freq_cur_id]-currents[max_freq_cur_id-cur_h])**2)
x0 = [max_freq, currents[np.nanargmax(res_freq_estimate)], np.sqrt(-d2fdI2/max_freq), 0.5, 0.5]
res_freq_cur_fit = leastsq(cost, x0)
plt.plot(currents, ft_x(currents, res_freq_cur_fit[0]))
plt.ylim([np.min(frequencies), np.max(frequencies)])
#plt.plot(currents, ft_x(currents, x0))
S21 = _S21

c:\python36\lib\site-packages\numpy\core\fromnumeric.py:2889: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
c:\python36\lib\site-packages\numpy\core\_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
c:\python36\lib\site-packages\ipykernel_launcher.py:82: RuntimeWarning: invalid value encountered in sqrt


In [9]:
res_freq_cur_fit

(array([  5.12808991e+09,  -1.13186206e-04,   8.20829356e+03,
          1.00250435e-01,   2.31468485e+00]), 1)

In [67]:
plt.figure()
#plt.plot(currents, np.real(Q))
plt.plot(currents, np.real(lifetime))
plt.ylim([0, 20e-9])
plt.grid()
plt.ylabel('Relaxation time, s')
plt.figure()
#plt.plot(currents, np.real(Q))
plt.plot(currents, np.real(C))
plt.ylim([-0.2e-9, 0.2e-9])
plt.grid()
plt.ylabel('Full resonator capacitance, F')
plt.figure()
#Lg = (res_freq_cur_fit[0][4]+1)/res_freq_cur_fit[0][4]*np.real(L)
#Lj = (res_freq_cur_fit[0][4]+1)*np.real(L)
plt.plot(currents, np.real(L), label='Full inductance')
#plt.plot(currents, np.real(Lg), label='Geometric inductance')
#plt.plot(currents, np.real(Lj), label='Josephson inductance')
plt.ylim([-0e-9, 0.2e-10])
plt.grid()
plt.ylabel('Resonator inductance, H')

In [8]:
Q_est = float(Q[max_freq_cur_id])
C_est = float(C[max_freq_cur_id])
L_est = float(L[max_freq_cur_id])
Lj = res_freq_cur_fit[0][4]/(res_freq_cur_fit[0][4]+1)*np.real(L_est)
Lg_est = np.real(L_est)/(res_freq_cur_fit[0][4]+1)
Ic = 1.054e-34/(2*1.6e-19*Lj)
print ('fr: {6:4.3g}, C: {0:4.2g} F, Lg: {1:4.2g} Hn, Lj: {2:4.2g} Hn, full SQUID Ic: {3:4.2g} A, asymmetry: {4:4.2f}, Q: {5:4.2f}'.format(\
        C_est, Lg_est, Lj, Ic, res_freq_cur_fit[0][3], Q_est, res_freq_cur_fit[0][0]))

fr: 5.13e+09, C: 1.5e-10 F, Lg: 1.9e-12 Hn, Lj: 4.5e-12 Hn, full SQUID Ic: 7.3e-05 A, asymmetry: 0.10, Q: 38.23


c:\python36\lib\site-packages\ipykernel_launcher.py:1: ComplexWarning: Casting complex values to real discards the imaginary part
  """Entry point for launching an IPython kernel.
c:\python36\lib\site-packages\ipykernel_launcher.py:2: ComplexWarning: Casting complex values to real discards the imaginary part
  
c:\python36\lib\site-packages\ipykernel_launcher.py:3: ComplexWarning: Casting complex values to real discards the imaginary part
  This is separate from the ipykernel package so we can avoid doing imports until


In [175]:
bgremove

array([  2.12221228e-03 +8.28879614e-04j,
         2.50260501e-03 -5.88461660e-04j,
         1.69399094e-03 -1.95215503e-03j,
        -2.40126198e-04 -2.81517223e-03j,
        -1.62253211e-03 -2.07307943e-03j,
        -1.92226369e-03 -6.35541743e-04j,
        -2.16575161e-03 +1.15822721e-03j,
        -1.14751056e-03 +1.07392832e-03j,
        -4.58683906e-04 +2.15715566e-03j,
         1.19493428e-03 +1.80242350e-03j,
         2.05764989e-03 +1.14208658e-03j,
         2.10304504e-03 -1.68959780e-04j,
         1.40100663e-03 -1.50440400e-03j,
         5.18023599e-04 -2.79801944e-03j,
        -1.30725427e-03 -3.09538996e-03j,
        -2.24986866e-03 -1.43606328e-03j,
        -2.35149513e-03 +7.71723086e-04j,
        -2.43764518e-03 +2.29205587e-03j,
        -9.35024795e-04 +2.72559592e-03j,
         8.24331364e-04 +2.32659808e-03j,
         2.69825912e-03 +1.75517534e-03j,
         2.84684721e-03 +3.70482613e-04j,
         2.76233489e-03 -1.44801809e-03j,
         1.11265880e-03 -2.6484020

In [ ]:
plt.figure()
plt.pcolormesh(np.abs(S21.T))
plt.figure()
plt.pcolormesh(np.angle(S21.T))

In [106]:
x0

[5096000000.0, -0.00011399999999999998, 13207.147529172158]

In [ ]:
fitresults